## Identifying and resolving conflicts in a batch of VI files

Andes Reinspection 
BGS 
Data information can be found at https://data.desi.lbl.gov/desi/spectro/prospect/target-reinspection-andes/

/global/cfs/cdirs/desi/spectro/redux/andes


448 visual inspections of a total of 150 unique objects

32 conflicts

In [1]:
save_filename='truth_table_Andes_reinspection_BGS_70500_20200303_1'

In [2]:
import os, sys, glob
import numpy as np

from astropy.io import fits
from astropy.table import Table, join, vstack
from astropy.io import fits

import pandas as pd
import fnmatch

import desispec.io

import VI_utils as VI
sys.path.append("/global/homes/r/tlan/prospect/prospect/py")

from prospect import utils_specviewer,plotframes
#import desispec
# library location will change ..
sys.path.append("/global/u2/t/tlan/python/prospect/py")
from prospect import utils_specviewer,plotframes
import matplotlib.pyplot as plt 

In [3]:
tiledir   = '/global/cfs/cdirs/desi/spectro/redux/andes/tiles/'
tiles = ['70500']
nights = ['20200303']
petals = ['0','1', '2', '3', '4', '5', '6' ,'7', '8', '9']
petals = ['0','3','6','7']
obs_db = utils_specviewer.make_targetdict(tiledir, petals=petals, tiles=tiles) # tiles = optional 
del obs_db['70500-20200228']
obs_db.keys()

dict_keys(['70500-20200303'])

In [4]:
pd.set_option('display.max_rows', 10)

In [5]:
#set to directory with all the VI files to merge
VI_dir = os.environ['HOME']+'/projects/VI_files/Andes_reinspection/BGS/'

In [6]:
#read a set of files 
all_files = os.listdir(VI_dir)
vi_files=[]

for i in range(1,4):
    pattern = "desi*_"+str(70500)+"*"+str(i)+"_*.csv"
    print(pattern)
    for entry in all_files:
        if fnmatch.fnmatch(entry, pattern):
            vi_files.append(entry)

print(vi_files)

desi*_70500*1_*.csv
desi*_70500*2_*.csv
desi*_70500*3_*.csv
['desi-vi_BGS_reinspection_70500_1_CHH.csv', 'desi-vi_BGS_reinspection_70500_1_AMA.csv', 'desi-vi_BGS_reinspection_70500_1_MJO.csv', 'desi-vi_BGS_reinspection_70500_2_AMA.csv', 'desi-vi_BGS_reinspection_70500_2_MJO.csv', 'desi-vi_BGS_reinspection_70500_2_CHH.csv', 'desi-vi_BGS_reinspection_70500_3_CHH.csv', 'desi-vi_BGS_reinspection_70500_3_MJO.csv', 'desi-vi_BGS_reinspection_70500_3_AMA.csv']


In [7]:
vi = pd.read_csv(VI_dir + vi_files[0], delimiter = ",", engine='python')
print(vi_files[0])
for i in range(1,len(vi_files)):
    print(vi_files[i])
    vi2 = pd.read_csv(VI_dir + vi_files[i], delimiter = ",", engine='python')
    vi = vi.append(vi2, ignore_index=True)
#print(vi)    
#make groups of visual inspections, grouped by unique objects, and state number of single and multiple VIs
vi_gp = vi.groupby(['TARGETID'])

print('There are ' + str(len(vi)) + ' visual inspections of a total of ' + str(len(vi_gp)) + ' unique objects')
print('That gives ' + str(len(vi)/len(vi_gp)) + ' inspections per object.')

desi-vi_BGS_reinspection_70500_1_CHH.csv
desi-vi_BGS_reinspection_70500_1_AMA.csv
desi-vi_BGS_reinspection_70500_1_MJO.csv
desi-vi_BGS_reinspection_70500_2_AMA.csv
desi-vi_BGS_reinspection_70500_2_MJO.csv
desi-vi_BGS_reinspection_70500_2_CHH.csv
desi-vi_BGS_reinspection_70500_3_CHH.csv
desi-vi_BGS_reinspection_70500_3_MJO.csv
desi-vi_BGS_reinspection_70500_3_AMA.csv
There are 450 visual inspections of a total of 150 unique objects
That gives 3.0 inspections per object.


In [8]:
#vi is a dataframe
display(vi)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
0    35191196661843077  52932  20200303   70500       0.34.4               -1   
1    35191196661843440  52932  20200303   70500       0.34.4               -1   
2    35191196661844537  52932  20200303   70500       0.34.4               -1   
3    35191196661845406  52932  20200303   70500       0.34.4               -1   
4    35191196666036608  52932  20200303   70500       0.34.4               -1   
..                 ...    ...       ...     ...          ...              ...   
445  35191220418382799  52932  20200303   70500       0.34.4               -1   
446  35191220418383876  52932  20200303   70500       0.34.4               -1   
447  35191220422576742  52932  20200303   70500       0.34.4               -1   
448  35191220422577184  52932  20200303   70500       0.34.4               -1   
449  35191220422577218  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
0                  -1           GALAXY     0.2732        CHH           1   
1                  -1           GALAXY     0.2080        CHH           3   
2                  -1           GALAXY     0.4338        CHH           4   
3                  -1           GALAXY     0.2381        CHH           3   
4                  -1              QSO     1.1471        CHH           1   
..                ...              ...        ...        ...         ...   
445                -1           GALAXY     0.1521        AMA           3   
446                -1           GALAXY     0.1148        AMA           3   
447                -1           GALAXY     0.1983        AMA           3   
448                -1           GALAXY     0.1340        AMA           4   
449                -1           GALAXY     0.1876        AMA           3   

    VI_issue  VI_z VI_spectype                           VI_comment  
0          C   NaN         NaN                                  NaN  
1        NaN   NaN         NaN                   Dn4000 + Continuum  
2        NaN   NaN         NaN               Halpha; SII; OII lines  
3        NaN   NaN         NaN           H;K absorption + continuum  
4         CS   NaN         NaN                      strange spectra  
..       ...   ...         ...                                  ...  
445      NaN   NaN         NaN                                  NaN  
446      NaN   NaN         NaN                                  NaN  
447      NaN   NaN         NaN                                  NaN  
448      NaN   NaN         NaN                                  NaN  
449      NaN   NaN         NaN  weak but apparent emission features  

[450 rows x 15 columns]

In [9]:
vi.keys()
len(vi)

450

# Merge with zbest files
#Add: fiberID, delta_chi2, flux information,.. anything else?


In [10]:

#read in fibermap info, loop over the files for all the petals
tf = Table.read(tiledir+'/'+tiles[0] + '/'+nights[0]+'/zbest-'+str(petals[0])+'-'+str(tiles[0])+'-'+nights[0]+'.fits',hdu='FIBERMAP')
tspec = Table.read(tiledir+'/'+tiles[0] + '/'+nights[0]+'/zbest-'+str(petals[0])+'-'+str(tiles[0])+'-'+nights[0]+'.fits',hdu='ZBEST')

for i in range(1,len(petals)):
    tn = Table.read(tiledir+'/'+tiles[0] + '/'+nights[0]+'/zbest-'+str(petals[i])+'-'+str(tiles[0])+'-'+nights[0]+'.fits',hdu='ZBEST')
    tnf = Table.read(tiledir+'/'+tiles[0] + '/'+nights[0]+'/zbest-'+str(petals[i])+'-'+str(tiles[0])+'-'+nights[0]+'.fits',hdu='FIBERMAP')
    tspec = vstack([tspec,tn])
    tf = vstack([tf,tnf])

#tf['TARGETID','FIBER','FLUX_G','FLUX_R','FLUX_Z','FIBERFLUX_G','FIBERFLUX_R','FIBERFLUX_Z'].to_panda()    
EXPID = list(set(tf['EXPID']))[0]
tf = tf[tf['EXPID']==EXPID]
tspec_df = tspec['TARGETID','DELTACHI2' ].to_pandas()
tf_df = tf['TARGETID','FIBER','FLUX_G','FLUX_R','FLUX_Z','FIBERFLUX_G','FIBERFLUX_R','FIBERFLUX_Z'].to_pandas()
print(len(tspec_df))
print(len(tf_df))
#tf_df = tf_df.rename(columns={"TargetID": "TARGETID"})
#tspec_df = tspec_df.rename(columns={"TargetID": "TARGETID"})
#print(len(vi))
vi = vi.merge(tf_df, how='left', on='TARGETID')
vi = vi.merge(tspec_df, how='left', on='TARGETID')
print(len(vi))

2000
2000
450


In [11]:
print(vi.keys())
print(len(vi))
vi['best redshift']=vi['VI_z']

Index(['TARGETID', 'EXPID', 'NIGHT', 'TILEID', 'Spec_version',
       'Redrock_version', 'Template_version', 'Redrock_spectype', 'Redrock_z',
       'VI_scanner', 'VI_quality', 'VI_issue', 'VI_z', 'VI_spectype',
       'VI_comment', 'FIBER', 'FLUX_G', 'FLUX_R', 'FLUX_Z', 'FIBERFLUX_G',
       'FIBERFLUX_R', 'FIBERFLUX_Z', 'DELTACHI2'],
      dtype='object')
450


### Adding a bunch of useful columns

In [12]:
#vi['VI_z']
import VI_utils as VI
#vi['VI_z']
#bad_str = [s is None for s in vi['VI_comment']]
#vi['VI_comment'].isnull()
#bad_str = [s is None for s in vi['VI_comment']]
#print(bad_str)
#vi.loc[vi['VI_comment'].isnull(),'VI_comment']='--'
#vi['VI_comment']
#vi['all VI comments'] = vi.groupby('TARGETID')['VI_comment'].transform(lambda x: '|'.join(x))
#print(vi['all VI comments'])
vi = VI.prep_new_columns(vi)
#vi['best redshift'] = vi['VI_z']
#test = vi['VI_z']
#vi['best redshift'].isnull()
#vi.loc[vi['best redshift'].isnull(), 'best redshift'] = vi.loc[vi['best redshift'].isnull(), 'Redrock_z']
#vi['best redshift']

In [13]:
#check all the new columns (keys) have been added correctly
display(vi)
print(vi.keys())

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
0    35191196661843077  52932  20200303   70500       0.34.4               -1   
1    35191196661843440  52932  20200303   70500       0.34.4               -1   
2    35191196661844537  52932  20200303   70500       0.34.4               -1   
3    35191196661845406  52932  20200303   70500       0.34.4               -1   
4    35191196666036608  52932  20200303   70500       0.34.4               -1   
..                 ...    ...       ...     ...          ...              ...   
445  35191220418382799  52932  20200303   70500       0.34.4               -1   
446  35191220418383876  52932  20200303   70500       0.34.4               -1   
447  35191220422576742  52932  20200303   70500       0.34.4               -1   
448  35191220422577184  52932  20200303   70500       0.34.4               -1   
449  35191220422577218  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  \
0                  -1           GALAXY     0.2732        CHH  ...   
1                  -1           GALAXY     0.2080        CHH  ...   
2                  -1           GALAXY     0.4338        CHH  ...   
3                  -1           GALAXY     0.2381        CHH  ...   
4                  -1              QSO     1.1471        CHH  ...   
..                ...              ...        ...        ...  ...   
445                -1           GALAXY     0.1521        AMA  ...   
446                -1           GALAXY     0.1148        AMA  ...   
447                -1           GALAXY     0.1983        AMA  ...   
448                -1           GALAXY     0.1340        AMA  ...   
449                -1           GALAXY     0.1876        AMA  ...   

       DELTACHI2 best redshift  best spectype vi_combined_flag vi_diff  \
0      66.652988        0.2732         GALAXY         2.333333       3   
1     348.863147        0.2080         GALAXY         3.333333       1   
2     673.106780        0.4338         GALAXY         4.000000       0   
3    1130.680205        0.2381         GALAXY         3.333333       1   
4     100.769188        1.1471            QSO         1.333333       1   
..           ...           ...            ...              ...     ...   
445   837.397658        0.1521         GALAXY         3.666667       1   
446   957.042863        0.1148         GALAXY         3.666667       1   
447   344.319406        0.1983         GALAXY         3.000000       2   
448  1414.918964        0.1340         GALAXY         4.000000       0   
449   371.857344        0.1876         GALAXY         3.666667       1   

           dz  vi_combined_z  \
0    0.000000       0.273200   
1    0.001326       0.207467   
2    0.000000       0.433800   
3    0.000000       0.238100   
4    0.000000       1.147100   
..        ...            ...   
445  0.000000       0.152100   
446  0.000000       0.114800   
447  0.000000       0.198300   
448  0.000000       0.134000   
449  0.000000       0.187600   

                                       all VI comments  N_VI  merger comment  
0    --|possible H alpha emission feature; no 4000 ...     3            none  
1    Dn4000 + Continuum|Many weak absorption featur...     3            none  
2    Halpha; SII; OII lines|--|H&K + Ha + SII (+ G ...     3            none  
3    H;K absorption + continuum|Strong continuum; w...     3            none  
4        strange spectra|No C ||| or Mg || features|--     3            none  
..                                                 ...   ...             ...  
445  OII; Halpha; SII emission lines|seems OII doub...     3            none  
446  OII; Halpha emission lines; possible H; K; D a...     3            none  
447              no emission or absorption lines|--|--     3            none  
448  OII; Halpha; SII emission lines|OII doublet re...     3            none  
449  Hbeta; OIII; Halpha; SII emission liens; H; K ...     3         

Index(['TARGETID', 'EXPID', 'NIGHT', 'TILEID', 'Spec_version',
       'Redrock_version', 'Template_version', 'Redrock_spectype', 'Redrock_z',
       'VI_scanner', 'VI_quality', 'VI_issue', 'VI_z', 'VI_spectype',
       'VI_comment', 'FIBER', 'FLUX_G', 'FLUX_R', 'FLUX_Z', 'FIBERFLUX_G',
       'FIBERFLUX_R', 'FIBERFLUX_Z', 'DELTACHI2', 'best redshift',
       'best spectype', 'vi_combined_flag', 'vi_diff', 'dz', 'vi_combined_z',
       'all VI comments', 'N_VI', 'merger comment'],
      dtype='object')


Get a table that holds only the objects that have been inspected more than once, and for which the individual VI classifications differ by 2 or more, or delta z / (1 + z) > 0.0033, or there is disagreement in best spectype (these are the conflicts to resolve)

In [14]:
vi_gp = vi.groupby(['TARGETID'])
vi_conflict = VI.find_conflicts(vi_gp)

In [15]:
len(vi_gp)

150

Get the target IDs of the problematic objects and display in table form for a quick summary:

In [16]:
unique_targets = np.unique(vi_conflict['TARGETID'].tolist())
print('Targets with problematic VI: ', unique_targets)
print('Total number of conflicts to resolve: ', len(unique_targets))

Targets with problematic VI:  [35191196661843077 35191196666037382 35191196666037541 35191196666037909
 35191196670231408 35191196670233434 35191196670233946 35191196670234398
 35191196670234724 35191196674426156 35191196674426637 35191200671596699
 35191200671598066 35191200675791113 35191200675792042 35191200675792850
 35191200675792885 35191200675793098 35191200675793777 35191200675794354
 35191200679985444 35191200679985679 35191200679986377 35191200679986445
 35191200679986644 35191200679986752 35191200679988159 35191200679988196
 35191204660380487 35191204660381031 35191204664574094 35191204664575007
 35191204664576079 35191204668769563 35191204668771151 35191204668772416
 35191208632387461 35191208632388250 35191208632389009 35191208636583994
 35191212583422687 35191212583422940 35191212583423743 35191212587616712
 35191216513484015 35191216513485304 35191220401604151 35191220401605015
 35191220401605130 35191220409992975 35191220409993084 35191220414188015
 35191220414188963 35

In [17]:
unique_targets[1]

35191196666037382

## This is where I resolve things manually - with care!!
### I think it's better to keep it in a notebook, as typos can be backtracked rather than a single manual edit of a text file

We edit either 'VI class', or 'best redshift' to resolve conflict. At the end, we look for conflicts again and we should find none.


In [18]:
#function to display the conflict in table format and open a prospect window
def display_conflict(conflict_id, show_spectra=None):
    
    #first, remind myself of the problem:
    display(vi[vi.TARGETID==unique_targets[conflict_id]][['TARGETID', 
       'Redrock_spectype', 'Redrock_z', 'VI_scanner', 'VI_quality', 'VI_issue',
       'VI_z', 'VI_spectype', 'VI_comment',
       'best redshift', 'best spectype', 'vi_combined_flag', 'vi_diff',
       'vi_combined_z', 'dz', 'all VI comments', 'N_VI', 'merger comment']])

    spectra, zcat= utils_specviewer.load_spectra_zcat_from_targets([unique_targets[conflict_id]], tiledir, obs_db)
    # VI interface in notebook
    if show_spectra:
        plotframes.plotspectra(spectra, zcatalog=zcat, title='Target_select', notebook=True, mask_type='CMX_TARGET',with_vi_widgets=False)

In [19]:
#first, keep a safe copy of the original dataframe
vi_safe = vi.copy()

We will inspect each conflict on a prospect window, and resolve each conflict in turn

In [20]:
show_spectra = False

In [21]:
#Keep track of the conflicts by conflict_id

#copy this text to a new cell to display the conflict
conflict_id=0
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
0    35191196661843077           GALAXY     0.2732        CHH           1   
50   35191196661843077           GALAXY     0.2732        AMA           2   
100  35191196661843077           GALAXY     0.2732        MJO           4   

    VI_issue  VI_z VI_spectype  \
0          C   NaN         NaN   
50       NaN   NaN         NaN   
100        R   NaN         NaN   

                                            VI_comment  best redshift  \
0                                                   --         0.2732   
50   possible H alpha emission feature; no 4000 Ang...         0.2732   
100                                           Ha + SII         0.2732   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
0          GALAXY          2.333333        3         0.2732  0.0   
50         GALAXY          2.333333        3         0.2732  0.0   
100        GALAXY          2.333333        3         0.2732  0.0   

                                       all VI comments  N_VI merger comment  
0    --|possible H alpha emission feature; no 4000 ...     3           none  
50   --|possible H alpha emission feature; no 4000 ...     3           none  
100  --|possible H alpha emission feature; no 4000 ...     3           none

In [22]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in quality. redshift is secure. Ha and SII and OII'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print(vi[vi.TARGETID==unique_targets[conflict_id]]['VI_quality'])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
0    35191196661843077  52932  20200303   70500       0.34.4               -1   
50   35191196661843077  52932  20200303   70500       0.34.4               -1   
100  35191196661843077  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
0                  -1           GALAXY     0.2732        CHH  ...  66.652988   
50                 -1           GALAXY     0.2732        AMA  ...  66.652988   
100                -1           GALAXY     0.2732        MJO  ...  66.652988   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
0          0.2732         GALAXY         2.333333       3  0.0         0.2732   
50         0.2732         GALAXY         2.333333       3  0.0         0.2732   
100        0.2732         GALAXY         2.333333       3  0.0         0.2732   

                                       all VI comments  N_VI  \
0    --|possible H alpha emission feature; no 4000 ...     3   
50   --|possible H alpha emission feature; no 4000 ...     3   
100  --|possible H alpha emission feature; no 4000 ...     3   

                                        merger comment  
0    disagreement in quality. redshift is secure. H...  
50   disagreement in quality. redshift is secure. H...  
100  disagreement in quality. redshift is secure. H...  

[3 rows x 32 columns]

0      4
50     4
100    4
Name: VI_quality, dtype: int64
conflict ID =  0


In [23]:
#copy this text to a new cell to display the conflict
conflict_id=1
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
5    35191196666037382              QSO     1.1514        CHH           1   
55   35191196666037382              QSO     1.1514        AMA           3   
105  35191196666037382              QSO     1.1514        MJO           1   

    VI_issue  VI_z VI_spectype                                VI_comment  \
5          S   NaN         NaN  possible spectrograph calibration issue?   
55       NaN   NaN         NaN           uncertain C|||; Mg || emissions   
105        R   NaN         NaN                                        --   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
5           1.1514           QSO          1.666667        2         1.1514   
55          1.1514           QSO          1.666667        2         1.1514   
105         1.1514           QSO          1.666667        2         1.1514   

      dz                                    all VI comments  N_VI  \
5    0.0  possible spectrograph calibration issue?|uncer...     3   
55   0.0  possible spectrograph calibration issue?|uncer...     3   
105  0.0  possible spectrograph calibration issue?|uncer...     3   

    merger comment  
5             none  
55            none  
105           none

In [24]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] =1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Quality disagreement. The best-fit is driven by calibration. No obvious features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print(vi[vi.TARGETID==unique_targets[conflict_id]]['VI_quality'])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
5    35191196666037382  52932  20200303   70500       0.34.4               -1   
55   35191196666037382  52932  20200303   70500       0.34.4               -1   
105  35191196666037382  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
5                  -1              QSO     1.1514        CHH  ...  136.73265   
55                 -1              QSO     1.1514        AMA  ...  136.73265   
105                -1              QSO     1.1514        MJO  ...  136.73265   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
5          1.1514            QSO         1.666667       2  0.0         1.1514   
55         1.1514            QSO         1.666667       2  0.0         1.1514   
105        1.1514            QSO         1.666667       2  0.0         1.1514   

                                       all VI comments  N_VI  \
5    possible spectrograph calibration issue?|uncer...     3   
55   possible spectrograph calibration issue?|uncer...     3   
105  possible spectrograph calibration issue?|uncer...     3   

                                        merger comment  
5    Quality disagreement. The best-fit is driven b...  
55   Quality disagreement. The best-fit is driven b...  
105  Quality disagreement. The best-fit is driven b...  

[3 rows x 32 columns]

5      1
55     1
105    1
Name: VI_quality, dtype: int64
conflict ID =  1


In [25]:
#copy this text to a new cell to display the conflict
conflict_id=2
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
6    35191196666037541           GALAXY     1.1685        CHH           1   
56   35191196666037541           GALAXY     1.1685        AMA           3   
106  35191196666037541           GALAXY     1.1685        MJO           4   

    VI_issue   VI_z VI_spectype  \
6          S    NaN         NaN   
56       NaN    NaN         NaN   
106       RS  0.232         NaN   

                                            VI_comment  best redshift  \
6    possible spectrograph calibration issue; spuri...         1.1685   
56       O || emission present; no 4000 angstrom break         1.1685   
106  a sudden drop between blue and red arms + Ha +...         0.2320   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
6          GALAXY          2.666667        3         1.1685  0.760146   
56         GALAXY          2.666667        3         1.1685  0.760146   
106        GALAXY          2.666667        3         1.1685  0.760146   

                                       all VI comments  N_VI merger comment  
6    possible spectrograph calibration issue; spuri...     3           none  
56   possible spectrograph calibration issue; spuri...     3           none  
106  possible spectrograph calibration issue; spuri...     3           none

In [26]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2320
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in quality. z is secure. Bad calibration'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
6    35191196666037541  52932  20200303   70500       0.34.4               -1   
56   35191196666037541  52932  20200303   70500       0.34.4               -1   
106  35191196666037541  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
6                  -1           GALAXY     1.1685        CHH  ...  528.315635   
56                 -1           GALAXY     1.1685        AMA  ...  528.315635   
106                -1           GALAXY     1.1685        MJO  ...  528.315635   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
6           0.232         GALAXY         2.666667       3  0.760146   
56          0.232         GALAXY         2.666667       3  0.760146   
106         0.232         GALAXY         2.666667       3  0.760146   

     vi_combined_z                                    all VI comments  N_VI  \
6           1.1685  possible spectrograph calibration issue; spuri...     3   
56          1.1685  possible spectrograph calibration issue; spuri...     3   
106         1.1685  possible spectrograph calibration issue; spuri...     3   

                                        merger comment  
6    disagreement in quality. z is secure. Bad cali...  
56   disagreement in quality. z is secure. Bad cali...  
106  disagreement in quality. z is secure. Bad cali...  

[3 rows x 32 columns]

conflict ID =  2


In [27]:
#copy this text to a new cell to display the conflict
conflict_id=3
display_conflict(conflict_id, show_spectra=True)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
7    35191196666037909           GALAXY     0.3195        CHH           2   
57   35191196666037909           GALAXY     0.3195        AMA           3   
107  35191196666037909           GALAXY     0.3195        MJO           1   

    VI_issue  VI_z VI_spectype  \
7        NaN   NaN         NaN   
57       NaN   NaN         NaN   
107        R   NaN         NaN   

                                            VI_comment  best redshift  \
7    no emission or absorption line features; but c...         0.3195   
57                                                  --         0.3195   
107  In this set many bestfit models seem to fail t...         0.3195   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
7          GALAXY               2.0        2         0.3195  0.0   
57         GALAXY               2.0        2         0.3195  0.0   
107        GALAXY               2.0        2         0.3195  0.0   

                                       all VI comments  N_VI merger comment  
7    no emission or absorption line features; but c...     3           none  
57   no emission or absorption line features; but c...     3           none  
107  no emission or absorption line features; but c...     3           none

Loading BokehJS ...

In [28]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 0.5128
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY' 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in quality. bad calibration driving the best fit'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print(vi[vi.TARGETID==unique_targets[conflict_id]]['VI_quality'])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
7    35191196666037909  52932  20200303   70500       0.34.4               -1   
57   35191196666037909  52932  20200303   70500       0.34.4               -1   
107  35191196666037909  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
7                  -1           GALAXY     0.3195        CHH  ...  329.034159   
57                 -1           GALAXY     0.3195        AMA  ...  329.034159   
107                -1           GALAXY     0.3195        MJO  ...  329.034159   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
7          0.3195         GALAXY              2.0       2  0.0         0.3195   
57         0.3195         GALAXY              2.0       2  0.0         0.3195   
107        0.3195         GALAXY              2.0       2  0.0         0.3195   

                                       all VI comments  N_VI  \
7    no emission or absorption line features; but c...     3   
57   no emission or absorption line features; but c...     3   
107  no emission or absorption line features; but c...     3   

                                        merger comment  
7    disagreement in quality. bad calibration drivi...  
57   disagreement in quality. bad calibration drivi...  
107  disagreement in quality. bad calibration drivi...  

[3 rows x 32 columns]

7      1
57     1
107    1
Name: VI_quality, dtype: int64
conflict ID =  3


In [29]:
#copy this text to a new cell to display the conflict
conflict_id=4
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
13   35191196670231408           GALAXY      0.576        CHH           2   
63   35191196670231408           GALAXY      0.576        AMA           2   
113  35191196670231408           GALAXY      0.576        MJO           4   

    VI_issue  VI_z VI_spectype  \
13       NaN   NaN         NaN   
63       NaN   NaN         NaN   
113       RS   NaN         NaN   

                                            VI_comment  best redshift  \
13   no emission or absorption lines; featureless c...          0.576   
63                                  no strong features          0.576   
113  In this set many bestfit models seem to fail t...          0.576   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
13         GALAXY          2.666667        2          0.576  0.0   
63         GALAXY          2.666667        2          0.576  0.0   
113        GALAXY          2.666667        2          0.576  0.0   

                                       all VI comments  N_VI merger comment  
13   no emission or absorption lines; featureless c...     3           none  
63   no emission or absorption lines; featureless c...     3           none  
113  no emission or absorption lines; featureless c...     3           none

In [30]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 1.3210
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag. Ca H and K MgI looks good'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print(vi[vi.TARGETID==unique_targets[conflict_id]]['VI_quality'])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
13   35191196670231408  52932  20200303   70500       0.34.4               -1   
63   35191196670231408  52932  20200303   70500       0.34.4               -1   
113  35191196670231408  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
13                 -1           GALAXY      0.576        CHH  ...  113.42886   
63                 -1           GALAXY      0.576        AMA  ...  113.42886   
113                -1           GALAXY      0.576        MJO  ...  113.42886   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
13          0.576         GALAXY         2.666667       2  0.0          0.576   
63          0.576         GALAXY         2.666667       2  0.0          0.576   
113         0.576         GALAXY         2.666667       2  0.0          0.576   

                                       all VI comments  N_VI  \
13   no emission or absorption lines; featureless c...     3   
63   no emission or absorption lines; featureless c...     3   
113  no emission or absorption lines; featureless c...     3   

                                      merger comment  
13   disagreement in flag. Ca H and K MgI looks good  
63   disagreement in flag. Ca H and K MgI looks good  
113  disagreement in flag. Ca H and K MgI looks good  

[3 rows x 32 columns]

13     4
63     4
113    4
Name: VI_quality, dtype: int64
conflict ID =  4


In [31]:
#copy this text to a new cell to display the conflict
conflict_id=5
display_conflict(conflict_id, show_spectra=True)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
20   35191196670233434           GALAXY     0.2302        CHH           2   
70   35191196670233434           GALAXY     0.2302        AMA           2   
120  35191196670233434           GALAXY     0.2302        MJO           4   

    VI_issue  VI_z VI_spectype  \
20       NaN   NaN         NaN   
70       NaN   NaN         NaN   
120       RS   NaN         NaN   

                                         VI_comment  best redshift  \
20   possible H;K absorption; featureless continuum         0.2302   
70               continuum good; no strong features         0.2302   
120                               H&K + G + MgI + D         0.2302   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
20         GALAXY          2.666667        2         0.2302  0.0   
70         GALAXY          2.666667        2         0.2302  0.0   
120        GALAXY          2.666667        2         0.2302  0.0   

                                       all VI comments  N_VI merger comment  
20   possible H;K absorption; featureless continuum...     3           none  
70   possible H;K absorption; featureless continuum...     3           none  
120  possible H;K absorption; featureless continuum...     3           none

Loading BokehJS ...

In [32]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag. Spectrum looks strange. Calibration issues. Take low quality'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
20   35191196670233434  52932  20200303   70500       0.34.4               -1   
70   35191196670233434  52932  20200303   70500       0.34.4               -1   
120  35191196670233434  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
20                 -1           GALAXY     0.2302        CHH  ...  75.477764   
70                 -1           GALAXY     0.2302        AMA  ...  75.477764   
120                -1           GALAXY     0.2302        MJO  ...  75.477764   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
20         0.2302         GALAXY         2.666667       2  0.0         0.2302   
70         0.2302         GALAXY         2.666667       2  0.0         0.2302   
120        0.2302         GALAXY         2.666667       2  0.0         0.2302   

                                       all VI comments  N_VI  \
20   possible H;K absorption; featureless continuum...     3   
70   possible H;K absorption; featureless continuum...     3   
120  possible H;K absorption; featureless continuum...     3   

                                        merger comment  
20   disagreement in flag. Spectrum looks strange. ...  
70   disagreement in flag. Spectrum looks strange. ...  
120  disagreement in flag. Spectrum looks strange. ...  

[3 rows x 32 columns]

conflict ID =  5


In [33]:
#copy this text to a new cell to display the conflict
conflict_id=6
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
23   35191196670233946           GALAXY     0.5592        CHH           3   
73   35191196670233946           GALAXY     0.5592        AMA           2   
123  35191196670233946           GALAXY     0.5592        MJO           4   

    VI_issue  VI_z VI_spectype  \
23       NaN   NaN         NaN   
73       NaN   NaN         NaN   
123       RS   NaN         NaN   

                                            VI_comment  best redshift  \
23                H; K; absorption; okay continuum fit         0.5592   
73                          model misses Mg || feature         0.5592   
123  In this set many bestfit models seem to fail t...         0.5592   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
23         GALAXY               3.0        2         0.5592  0.0   
73         GALAXY               3.0        2         0.5592  0.0   
123        GALAXY               3.0        2         0.5592  0.0   

                                       all VI comments  N_VI merger comment  
23   H; K; absorption; okay continuum fit|model mis...     3           none  
73   H; K; absorption; okay continuum fit|model mis...     3           none  
123  H; K; absorption; okay continuum fit|model mis...     3           none

In [34]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 1.5
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Clear 4000 break'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
23   35191196670233946  52932  20200303   70500       0.34.4               -1   
73   35191196670233946  52932  20200303   70500       0.34.4               -1   
123  35191196670233946  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
23                 -1           GALAXY     0.5592        CHH  ...  149.306005   
73                 -1           GALAXY     0.5592        AMA  ...  149.306005   
123                -1           GALAXY     0.5592        MJO  ...  149.306005   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
23         0.5592         GALAXY              3.0       2  0.0         0.5592   
73         0.5592         GALAXY              3.0       2  0.0         0.5592   
123        0.5592         GALAXY              3.0       2  0.0         0.5592   

                                       all VI comments  N_VI    merger comment  
23   H; K; absorption; okay continuum fit|model mis...     3  Clear 4000 break  
73   H; K; absorption; okay continuum fit|model mis...     3  Clear 4000 break  
123  H; K; absorption; okay continuum fit|model mis...     3  Clear 4000 break  

[3 rows x 32 columns]

conflict ID =  6


In [35]:
#copy this text to a new cell to display the conflict
conflict_id=7
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
26   35191196670234398           GALAXY     0.4427        CHH           1   
76   35191196670234398           GALAXY     0.4427        AMA           3   
126  35191196670234398           GALAXY     0.4427        MJO           4   

    VI_issue    VI_z VI_spectype  \
26         S     NaN         NaN   
76       NaN     NaN         NaN   
126       RS  0.1847         NaN   

                                            VI_comment  best redshift  \
26                                                  --         0.4427   
76                                                  --         0.4427   
126  In this set many bestfit models seem to fail t...         0.1847   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
26         GALAXY          2.666667        3         0.4427  0.217777   
76         GALAXY          2.666667        3         0.4427  0.217777   
126        GALAXY          2.666667        3         0.4427  0.217777   

                                       all VI comments  N_VI merger comment  
26   --|--|In this set many bestfit models seem to ...     3           none  
76   --|--|In this set many bestfit models seem to ...     3           none  
126  --|--|In this set many bestfit models seem to ...     3           none

In [36]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.1847
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag. Calibration drives the best fit  Redshift is secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
26   35191196670234398  52932  20200303   70500       0.34.4               -1   
76   35191196670234398  52932  20200303   70500       0.34.4               -1   
126  35191196670234398  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
26                 -1           GALAXY     0.4427        CHH  ...  26.704723   
76                 -1           GALAXY     0.4427        AMA  ...  26.704723   
126                -1           GALAXY     0.4427        MJO  ...  26.704723   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
26         0.1847         GALAXY         2.666667       3  0.217777   
76         0.1847         GALAXY         2.666667       3  0.217777   
126        0.1847         GALAXY         2.666667       3  0.217777   

     vi_combined_z                                    all VI comments  N_VI  \
26          0.4427  --|--|In this set many bestfit models seem to ...     3   
76          0.4427  --|--|In this set many bestfit models seem to ...     3   
126         0.4427  --|--|In this set many bestfit models seem to ...     3   

                                        merger comment  
26   disagreement in flag. Calibration drives the b...  
76   disagreement in flag. Calibration drives the b...  
126  disagreement in flag. Calibration drives the b...  

[3 rows x 32 columns]

conflict ID =  7


In [37]:
#copy this text to a new cell to display the conflict
conflict_id=8
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
27   35191196670234724           GALAXY     1.1613        CHH           1   
77   35191196670234724           GALAXY     1.1613        AMA           2   
127  35191196670234724           GALAXY     1.1613        MJO           4   

    VI_issue    VI_z VI_spectype  \
27         S     NaN         NaN   
77       NaN     NaN         NaN   
127       RS  0.2288         NaN   

                                            VI_comment  best redshift  \
27                                                  --         1.1613   
77                       no strong absorption features         1.1613   
127  In this set many bestfit models seem to fail t...         0.2288   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z       dz  \
27         GALAXY          2.333333        3         1.1613  0.75887   
77         GALAXY          2.333333        3         1.1613  0.75887   
127        GALAXY          2.333333        3         1.1613  0.75887   

                                       all VI comments  N_VI merger comment  
27   --|no strong absorption features|In this set m...     3           none  
77   --|no strong absorption features|In this set m...     3           none  
127  --|no strong absorption features|In this set m...     3           none

In [38]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2288
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Redshift is secure. Calibration drvies the best'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
27   35191196670234724  52932  20200303   70500       0.34.4               -1   
77   35191196670234724  52932  20200303   70500       0.34.4               -1   
127  35191196670234724  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
27                 -1           GALAXY     1.1613        CHH  ...  1150.11705   
77                 -1           GALAXY     1.1613        AMA  ...  1150.11705   
127                -1           GALAXY     1.1613        MJO  ...  1150.11705   

    best redshift  best spectype vi_combined_flag vi_diff       dz  \
27         0.2288         GALAXY         2.333333       3  0.75887   
77         0.2288         GALAXY         2.333333       3  0.75887   
127        0.2288         GALAXY         2.333333       3  0.75887   

     vi_combined_z                                    all VI comments  N_VI  \
27          1.1613  --|no strong absorption features|In this set m...     3   
77          1.1613  --|no strong absorption features|In this set m...     3   
127         1.1613  --|no strong absorption features|In this set m...     3   

                                      merger comment  
27   Redshift is secure. Calibration drvies the best  
77   Redshift is secure. Calibration drvies the best  
127  Redshift is secure. Calibration drvies the best  

[3 rows x 32 columns]

conflict ID =  8


In [39]:
#copy this text to a new cell to display the conflict
conflict_id=9
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
29   35191196674426156           GALAXY     0.4575        CHH           2   
79   35191196674426156           GALAXY     0.4575        AMA           2   
129  35191196674426156           GALAXY     0.4575        MJO           4   

    VI_issue  VI_z VI_spectype  \
29       NaN   NaN         NaN   
79       NaN   NaN         NaN   
129        R   NaN         NaN   

                                            VI_comment  best redshift  \
29   no emission or absorption lines;  featureless ...         0.4575   
79                                                  --         0.4575   
129                                   H&K + 4000A + Ha         0.4575   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
29         GALAXY          2.666667        2         0.4575  0.0   
79         GALAXY          2.666667        2         0.4575  0.0   
129        GALAXY          2.666667        2         0.4575  0.0   

                                       all VI comments  N_VI merger comment  
29   no emission or absorption lines;  featureless ...     3           none  
79   no emission or absorption lines;  featureless ...     3           none  
129  no emission or absorption lines;  featureless ...     3           none

In [40]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag. Possible CaHK but not sure. Take low VI quality'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
29   35191196674426156  52932  20200303   70500       0.34.4               -1   
79   35191196674426156  52932  20200303   70500       0.34.4               -1   
129  35191196674426156  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
29                 -1           GALAXY     0.4575        CHH  ...  109.832082   
79                 -1           GALAXY     0.4575        AMA  ...  109.832082   
129                -1           GALAXY     0.4575        MJO  ...  109.832082   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
29         0.4575         GALAXY         2.666667       2  0.0         0.4575   
79         0.4575         GALAXY         2.666667       2  0.0         0.4575   
129        0.4575         GALAXY         2.666667       2  0.0         0.4575   

                                       all VI comments  N_VI  \
29   no emission or absorption lines;  featureless ...     3   
79   no emission or absorption lines;  featureless ...     3   
129  no emission or absorption lines;  featureless ...     3   

                                        merger comment  
29   disagreement in flag. Possible CaHK but not su...  
79   disagreement in flag. Possible CaHK but not su...  
129  disagreement in flag. Possible CaHK but not su...  

[3 rows x 32 columns]

conflict ID =  9


In [41]:
#copy this text to a new cell to display the conflict
conflict_id=10
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
31   35191196674426637           GALAXY     0.4572        CHH           4   
81   35191196674426637           GALAXY     0.4572        AMA           1   
131  35191196674426637           GALAXY     0.4572        MJO           4   

    VI_issue  VI_z VI_spectype                                  VI_comment  \
31       NaN   NaN         NaN  H; K; Mg; D absorption; good continuum fit   
81         C   NaN        STAR                 possible misclassification    
131        R   NaN         NaN                      H&K + Hb + MgI + D + G   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
31          0.4572        GALAXY               3.0        3         0.4572   
81          0.4572          STAR               3.0        3         0.4572   
131         0.4572        GALAXY               3.0        3         0.4572   

      dz                                    all VI comments  N_VI  \
31   0.0  H; K; Mg; D absorption; good continuum fit|pos...     3   
81   0.0  H; K; Mg; D absorption; good continuum fit|pos...     3   
131  0.0  H; K; Mg; D absorption; good continuum fit|pos...     3   

    merger comment  
31            none  
81            none  
131           none

In [42]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'flag disagreement. Passive galaxy'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
31   35191196674426637  52932  20200303   70500       0.34.4               -1   
81   35191196674426637  52932  20200303   70500       0.34.4               -1   
131  35191196674426637  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
31                 -1           GALAXY     0.4572        CHH  ...  912.679586   
81                 -1           GALAXY     0.4572        AMA  ...  912.679586   
131                -1           GALAXY     0.4572        MJO  ...  912.679586   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
31         0.4572         GALAXY              3.0       3  0.0         0.4572   
81         0.4572         GALAXY              3.0       3  0.0         0.4572   
131        0.4572         GALAXY              3.0       3  0.0         0.4572   

                                       all VI comments  N_VI  \
31   H; K; Mg; D absorption; good continuum fit|pos...     3   
81   H; K; Mg; D absorption; good continuum fit|pos...     3   
131  H; K; Mg; D absorption; good continuum fit|pos...     3   

                        merger comment  
31   flag disagreement. Passive galaxy  
81   flag disagreement. Passive galaxy  
131  flag disagreement. Passive galaxy  

[3 rows x 32 columns]

conflict ID =  10


In [43]:
#copy this text to a new cell to display the conflict
conflict_id=11
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
35   35191200671596699           GALAXY     1.1578        CHH           1   
85   35191200671596699           GALAXY     1.1578        AMA           2   
135  35191200671596699           GALAXY     1.1578        MJO           3   

    VI_issue    VI_z VI_spectype  \
35       NaN     NaN         NaN   
85       NaN     NaN         NaN   
135       RS  0.0662         NaN   

                                            VI_comment  best redshift  \
35   no emission or absorption lines; featureless c...         1.1578   
85                                  no strong features         1.1578   
135  In this set many bestfit models seem to fail t...         0.0662   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
35         GALAXY               2.0        2         1.1578  1.023823   
85         GALAXY               2.0        2         1.1578  1.023823   
135        GALAXY               2.0        2         1.1578  1.023823   

                                       all VI comments  N_VI merger comment  
35   no emission or absorption lines; featureless c...     3           none  
85   no emission or absorption lines; featureless c...     3           none  
135  no emission or absorption lines; featureless c...     3           none

In [44]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.0662
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Strange feature driving the best fit. best redshift is secure. Ha|[OII]'
#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
35   35191200671596699  52932  20200303   70500       0.34.4               -1   
85   35191200671596699  52932  20200303   70500       0.34.4               -1   
135  35191200671596699  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
35                 -1           GALAXY     1.1578        CHH  ...   4.993728   
85                 -1           GALAXY     1.1578        AMA  ...   4.993728   
135                -1           GALAXY     1.1578        MJO  ...   4.993728   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
35         0.0662         GALAXY              2.0       2  1.023823   
85         0.0662         GALAXY              2.0       2  1.023823   
135        0.0662         GALAXY              2.0       2  1.023823   

     vi_combined_z                                    all VI comments  N_VI  \
35          1.1578  no emission or absorption lines; featureless c...     3   
85          1.1578  no emission or absorption lines; featureless c...     3   
135         1.1578  no emission or absorption lines; featureless c...     3   

                                        merger comment  
35   Strange feature driving the best fit. best red...  
85   Strange feature driving the best fit. best red...  
135  Strange feature driving the best fit. best red...  

[3 rows x 32 columns]

conflict ID =  11


In [45]:
#copy this text to a new cell to display the conflict
conflict_id=12
display_conflict(conflict_id, show_spectra=show_spectra)



TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
40   35191200671598066           GALAXY     1.1454        CHH           1   
90   35191200671598066           GALAXY     1.1454        AMA           3   
140  35191200671598066           GALAXY     1.1454        MJO           1   

    VI_issue  VI_z VI_spectype  \
40       NaN   NaN         NaN   
90       NaN   NaN         NaN   
140       RS   NaN         NaN   

                                            VI_comment  best redshift  \
40   no emission or absorption lines; featureless c...         1.1454   
90                                                  --         1.1454   
140  In this set many bestfit models seem to fail t...         1.1454   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
40         GALAXY          1.666667        2         1.1454  0.0   
90         GALAXY          1.666667        2         1.1454  0.0   
140        GALAXY          1.666667        2         1.1454  0.0   

                                       all VI comments  N_VI merger comment  
40   no emission or absorption lines; featureless c...     3           none  
90   no emission or absorption lines; featureless c...     3           none  
140  no emission or absorption lines; featureless c...     3           none

In [46]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.0810
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Calibration driving best fit.disagreement in spectral type. Ha | NII | [S II]'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
40   35191200671598066  52932  20200303   70500       0.34.4               -1   
90   35191200671598066  52932  20200303   70500       0.34.4               -1   
140  35191200671598066  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
40                 -1           GALAXY     1.1454        CHH  ...  141.960295   
90                 -1           GALAXY     1.1454        AMA  ...  141.960295   
140                -1           GALAXY     1.1454        MJO  ...  141.960295   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
40          0.081         GALAXY         1.666667       2  0.0         1.1454   
90          0.081         GALAXY         1.666667       2  0.0         1.1454   
140         0.081         GALAXY         1.666667       2  0.0         1.1454   

                                       all VI comments  N_VI  \
40   no emission or absorption lines; featureless c...     3   
90   no emission or absorption lines; featureless c...     3   
140  no emission or absorption lines; featureless c...     3   

                                        merger comment  
40   Calibration driving best fit.disagreement in s...  
90   Calibration driving best fit.disagreement in s...  
140  Calibration driving best fit.disagreement in s...  

[3 rows x 32 columns]

conflict ID =  12


In [47]:
#copy this text to a new cell to display the conflict
conflict_id=13
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
42   35191200675791113           GALAXY     0.4181        CHH           1   
92   35191200675791113           GALAXY     0.4181        AMA           3   
142  35191200675791113           GALAXY     0.4181        MJO           2   

    VI_issue  VI_z VI_spectype  \
42       NaN   NaN         NaN   
92       NaN   NaN         NaN   
142       RS   NaN         NaN   

                                            VI_comment  best redshift  \
42   no emission or absorption lines; featureless c...         0.4181   
92   model does not match data well at smaller wave...         0.4181   
142  In this set many bestfit models seem to fail t...         0.4181   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
42         GALAXY               2.0        2         0.4181  0.0   
92         GALAXY               2.0        2         0.4181  0.0   
142        GALAXY               2.0        2         0.4181  0.0   

                                       all VI comments  N_VI merger comment  
42   no emission or absorption lines; featureless c...     3           none  
92   no emission or absorption lines; featureless c...     3           none  
142  no emission or absorption lines; featureless c...     3           none

In [48]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag. No obvious features. only flux. Calibration '

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
42   35191200675791113  52932  20200303   70500       0.34.4               -1   
92   35191200675791113  52932  20200303   70500       0.34.4               -1   
142  35191200675791113  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
42                 -1           GALAXY     0.4181        CHH  ...  75.922123   
92                 -1           GALAXY     0.4181        AMA  ...  75.922123   
142                -1           GALAXY     0.4181        MJO  ...  75.922123   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
42         0.4181         GALAXY              2.0       2  0.0         0.4181   
92         0.4181         GALAXY              2.0       2  0.0         0.4181   
142        0.4181         GALAXY              2.0       2  0.0         0.4181   

                                       all VI comments  N_VI  \
42   no emission or absorption lines; featureless c...     3   
92   no emission or absorption lines; featureless c...     3   
142  no emission or absorption lines; featureless c...     3   

                                        merger comment  
42   disagreement in flag. No obvious features. onl...  
92   disagreement in flag. No obvious features. onl...  
142  disagreement in flag. No obvious features. onl...  

[3 rows x 32 columns]

conflict ID =  13


In [49]:
#copy this text to a new cell to display the conflict
conflict_id=14
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
45   35191200675792042           GALAXY     0.4192        CHH           1   
95   35191200675792042           GALAXY     0.4192        AMA           3   
145  35191200675792042           GALAXY     0.4192        MJO           1   

    VI_issue  VI_z VI_spectype  \
45       NaN   NaN         NaN   
95       NaN   NaN         NaN   
145       RS   NaN         NaN   

                                            VI_comment  best redshift  \
45   no emission or absorption lines; bad continuum...         0.4192   
95                                                  --         0.4192   
145  In this set many bestfit models seem to fail t...         0.4192   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
45         GALAXY          1.666667        2         0.4192  0.0   
95         GALAXY          1.666667        2         0.4192  0.0   
145        GALAXY          1.666667        2         0.4192  0.0   

                                       all VI comments  N_VI merger comment  
45   no emission or absorption lines; bad continuum...     3           none  
95   no emission or absorption lines; bad continuum...     3           none  
145  no emission or absorption lines; bad continuum...     3           none

In [50]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'low S/N. Take low quality'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
45   35191200675792042  52932  20200303   70500       0.34.4               -1   
95   35191200675792042  52932  20200303   70500       0.34.4               -1   
145  35191200675792042  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
45                 -1           GALAXY     0.4192        CHH  ...  139.410811   
95                 -1           GALAXY     0.4192        AMA  ...  139.410811   
145                -1           GALAXY     0.4192        MJO  ...  139.410811   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
45         0.4192         GALAXY         1.666667       2  0.0         0.4192   
95         0.4192         GALAXY         1.666667       2  0.0         0.4192   
145        0.4192         GALAXY         1.666667       2  0.0         0.4192   

                                       all VI comments  N_VI  \
45   no emission or absorption lines; bad continuum...     3   
95   no emission or absorption lines; bad continuum...     3   
145  no emission or absorption lines; bad continuum...     3   

                merger comment  
45   low S/N. Take low quality  
95   low S/N. Take low quality  
145  low S/N. Take low quality  

[3 rows x 32 columns]

conflict ID =  14


In [51]:
#copy this text to a new cell to display the conflict
conflict_id=15
display_conflict(conflict_id, show_spectra=show_spectra)



TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
46   35191200675792850           GALAXY     0.5095        CHH           1   
96   35191200675792850           GALAXY     0.5095        AMA           2   
146  35191200675792850           GALAXY     0.5095        MJO           3   

    VI_issue   VI_z VI_spectype  \
46       NaN    NaN         NaN   
96       NaN    NaN         NaN   
146        R  0.118         NaN   

                                            VI_comment  best redshift  \
46   no emission or absorption lines; featureless c...         0.5095   
96                                  no strong features         0.5095   
146                                           Ha + SII         0.1180   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
46         GALAXY               2.0        2         0.5095  0.350179   
96         GALAXY               2.0        2         0.5095  0.350179   
146        GALAXY               2.0        2         0.5095  0.350179   

                                       all VI comments  N_VI merger comment  
46   no emission or absorption lines; featureless c...     3           none  
96   no emission or absorption lines; featureless c...     3           none  
146  no emission or absorption lines; featureless c...     3           none

In [52]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.1180
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration | redshift secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
46   35191200675792850  52932  20200303   70500       0.34.4               -1   
96   35191200675792850  52932  20200303   70500       0.34.4               -1   
146  35191200675792850  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
46                 -1           GALAXY     0.5095        CHH  ...  407.425796   
96                 -1           GALAXY     0.5095        AMA  ...  407.425796   
146                -1           GALAXY     0.5095        MJO  ...  407.425796   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
46          0.118         GALAXY              2.0       2  0.350179   
96          0.118         GALAXY              2.0       2  0.350179   
146         0.118         GALAXY              2.0       2  0.350179   

     vi_combined_z                                    all VI comments  N_VI  \
46          0.5095  no emission or absorption lines; featureless c...     3   
96          0.5095  no emission or absorption lines; featureless c...     3   
146         0.5095  no emission or absorption lines; featureless c...     3   

                        merger comment  
46   Bad calibration | redshift secure  
96   Bad calibration | redshift secure  
146  Bad calibration | redshift secure  

[3 rows x 32 columns]

conflict ID =  15


In [53]:
#copy this text to a new cell to display the conflict
conflict_id=16
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
47   35191200675792885           GALAXY     0.4047        CHH           3   
97   35191200675792885           GALAXY     0.4047        AMA           2   
147  35191200675792885           GALAXY     0.4047        MJO           4   

    VI_issue  VI_z VI_spectype  \
47       NaN   NaN         NaN   
97       NaN   NaN         NaN   
147        R   NaN         NaN   

                                            VI_comment  best redshift  \
47   OII; Halpha; SII emission lines; featureless c...         0.4047   
97             likely H alpha emission; weak continuum         0.4047   
147                               Ha + SII + continuum         0.4047   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
47         GALAXY               3.0        2         0.4047  0.0   
97         GALAXY               3.0        2         0.4047  0.0   
147        GALAXY               3.0        2         0.4047  0.0   

                                       all VI comments  N_VI merger comment  
47   OII; Halpha; SII emission lines; featureless c...     3           none  
97   OII; Halpha; SII emission lines; featureless c...     3           none  
147  OII; Halpha; SII emission lines; featureless c...     3           none

In [54]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 0.2409
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag, z is secure. Ha SII'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
47   35191200675792885  52932  20200303   70500       0.34.4               -1   
97   35191200675792885  52932  20200303   70500       0.34.4               -1   
147  35191200675792885  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
47                 -1           GALAXY     0.4047        CHH  ...  680.236388   
97                 -1           GALAXY     0.4047        AMA  ...  680.236388   
147                -1           GALAXY     0.4047        MJO  ...  680.236388   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
47         0.4047         GALAXY              3.0       2  0.0         0.4047   
97         0.4047         GALAXY              3.0       2  0.0         0.4047   
147        0.4047         GALAXY              3.0       2  0.0         0.4047   

                                       all VI comments  N_VI  \
47   OII; Halpha; SII emission lines; featureless c...     3   
97   OII; Halpha; SII emission lines; featureless c...     3   
147  OII; Halpha; SII emission lines; featureless c...     3   

                                merger comment  
47   disagreement in flag, z is secure. Ha SII  
97   disagreement in flag, z is secure. Ha SII  
147  disagreement in flag, z is secure. Ha SII  

[3 rows x 32 columns]

conflict ID =  16


In [55]:
#copy this text to a new cell to display the conflict
conflict_id=17
display_conflict(conflict_id, show_spectra=show_spectra)



TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
48   35191200675793098              QSO     1.1831        CHH           1   
98   35191200675793098              QSO     1.1831        AMA           3   
148  35191200675793098              QSO     1.1831        MJO           1   

    VI_issue  VI_z VI_spectype  \
48       NaN   NaN         NaN   
98       NaN   NaN         NaN   
148        R   NaN         NaN   

                                            VI_comment  best redshift  \
48   no emission or absorption lines; featureless c...         1.1831   
98                                                  --         1.1831   
148  In this set many bestfit models seem to fail t...         1.1831   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
48            QSO          1.666667        2         1.1831  0.0   
98            QSO          1.666667        2         1.1831  0.0   
148           QSO          1.666667        2         1.1831  0.0   

                                       all VI comments  N_VI merger comment  
48   no emission or absorption lines; featureless c...     3           none  
98   no emission or absorption lines; featureless c...     3           none  
148  no emission or absorption lines; featureless c...     3           none

In [56]:
#copy this text to a new cell to resolve the conflict

vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. only flyx'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
48   35191200675793098  52932  20200303   70500       0.34.4               -1   
98   35191200675793098  52932  20200303   70500       0.34.4               -1   
148  35191200675793098  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
48                 -1              QSO     1.1831        CHH  ...  71.065825   
98                 -1              QSO     1.1831        AMA  ...  71.065825   
148                -1              QSO     1.1831        MJO  ...  71.065825   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
48         1.1831            QSO         1.666667       2  0.0         1.1831   
98         1.1831            QSO         1.666667       2  0.0         1.1831   
148        1.1831            QSO         1.666667       2  0.0         1.1831   

                                       all VI comments  N_VI  \
48   no emission or absorption lines; featureless c...     3   
98   no emission or absorption lines; featureless c...     3   
148  no emission or absorption lines; featureless c...     3   

                 merger comment  
48   Bad calibration. only flyx  
98   Bad calibration. only flyx  
148  Bad calibration. only flyx  

[3 rows x 32 columns]

conflict ID =  17


In [57]:
#copy this text to a new cell to display the conflict
conflict_id=18
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
151  35191200675793777           GALAXY     0.6655        AMA           1   
201  35191200675793777           GALAXY     0.6655        MJO           4   
251  35191200675793777           GALAXY     0.6655        CHH           1   

    VI_issue    VI_z VI_spectype  \
151      NaN     NaN         NaN   
201        R  0.0948         NaN   
251      NaN     NaN         NaN   

                                            VI_comment  best redshift  \
151  no emission/absorption features present; uncer...         0.6655   
201                               OII + Ha (+ G + MgI)         0.0948   
251  no emission or absorption lines; featureless c...         0.6655   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
151        GALAXY               2.0        3         0.6655  0.521282   
201        GALAXY               2.0        3         0.6655  0.521282   
251        GALAXY               2.0        3         0.6655  0.521282   

                                       all VI comments  N_VI merger comment  
151  no emission/absorption features present; uncer...     3           none  
201  no emission/absorption features present; uncer...     3           none  
251  no emission/absorption features present; uncer...     3           none

In [58]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.0948
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'disagreement in flag. Redshift is secure. Bad Calibration'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
151  35191200675793777  52932  20200303   70500       0.34.4               -1   
201  35191200675793777  52932  20200303   70500       0.34.4               -1   
251  35191200675793777  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
151                -1           GALAXY     0.6655        AMA  ...   9.257388   
201                -1           GALAXY     0.6655        MJO  ...   9.257388   
251                -1           GALAXY     0.6655        CHH  ...   9.257388   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
151        0.0948         GALAXY              2.0       3  0.521282   
201        0.0948         GALAXY              2.0       3  0.521282   
251        0.0948         GALAXY              2.0       3  0.521282   

     vi_combined_z                                    all VI comments  N_VI  \
151         0.6655  no emission/absorption features present; uncer...     3   
201         0.6655  no emission/absorption features present; uncer...     3   
251         0.6655  no emission/absorption features present; uncer...     3   

                                        merger comment  
151  disagreement in flag. Redshift is secure. Bad ...  
201  disagreement in flag. Redshift is secure. Bad ...  
251  disagreement in flag. Redshift is secure. Bad ...  

[3 rows x 32 columns]

conflict ID =  18


In [59]:
#copy this text to a new cell to display the conflict
conflict_id=19
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
152  35191200675794354           GALAXY     0.3481        AMA           2   
202  35191200675794354           GALAXY     0.3481        MJO           3   
252  35191200675794354           GALAXY     0.3481        CHH           1   

    VI_issue  VI_z VI_spectype  \
152      NaN   NaN         NaN   
202        R   NaN         NaN   
252      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
152                                 no strong features         0.3481   
202  H&K + MgI + weak Ha / jump between blue and re...         0.3481   
252  no emission or absorption lines; featureless c...         0.3481   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
152        GALAXY               2.0        2         0.3481  0.0   
202        GALAXY               2.0        2         0.3481  0.0   
252        GALAXY               2.0        2         0.3481  0.0   

                                       all VI comments  N_VI merger comment  
152  no strong features|H&K + MgI + weak Ha / jump ...     3           none  
202  no strong features|H&K + MgI + weak Ha / jump ...     3           none  
252  no strong features|H&K + MgI + weak Ha / jump ...     3           none

In [60]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 0.7812
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. Possible absorption features. Take median'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)



TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
152  35191200675794354  52932  20200303   70500       0.34.4               -1   
202  35191200675794354  52932  20200303   70500       0.34.4               -1   
252  35191200675794354  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
152                -1           GALAXY     0.3481        AMA  ...  24.601251   
202                -1           GALAXY     0.3481        MJO  ...  24.601251   
252                -1           GALAXY     0.3481        CHH  ...  24.601251   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
152        0.3481         GALAXY              2.0       2  0.0         0.3481   
202        0.3481         GALAXY              2.0       2  0.0         0.3481   
252        0.3481         GALAXY              2.0       2  0.0         0.3481   

                                       all VI comments  N_VI  \
152  no strong features|H&K + MgI + weak Ha / jump ...     3   
202  no strong features|H&K + MgI + weak Ha / jump ...     3   
252  no strong features|H&K + MgI + weak Ha / jump ...     3   

                                        merger comment  
152  Bad calibration. Possible absorption features....  
202  Bad calibration. Possible absorption features....  
252  Bad calibration. Possible absorption features....  

[3 rows x 32 columns]

conflict ID =  19


In [61]:
#copy this text to a new cell to display the conflict
conflict_id=20
display_conflict(conflict_id, show_spectra=show_spectra)

TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
154  35191200679985444           GALAXY     0.4591        AMA           2   
204  35191200679985444           GALAXY     0.4591        MJO           3   
254  35191200679985444           GALAXY     0.4591        CHH           1   

    VI_issue  VI_z VI_spectype  \
154        S   NaN         NaN   
204        R   NaN         NaN   
254        S   NaN         NaN   

                                            VI_comment  best redshift  \
154                            unknown break at 9000 A         0.4591   
204  pipeline fit doesn't work well for the continu...         0.4591   
254  no emission or absorption lines; featureless c...         0.4591   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
154        GALAXY               2.0        2         0.4591  0.0   
204        GALAXY               2.0        2         0.4591  0.0   
254        GALAXY               2.0        2         0.4591  0.0   

                                       all VI comments  N_VI merger comment  
154  unknown break at 9000 A|pipeline fit doesn't w...     3           none  
204  unknown break at 9000 A|pipeline fit doesn't w...     3           none  
254  unknown break at 9000 A|pipeline fit doesn't w...     3           none

In [62]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 0.862
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. Possible absorption features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
154  35191200679985444  52932  20200303   70500       0.34.4               -1   
204  35191200679985444  52932  20200303   70500       0.34.4               -1   
254  35191200679985444  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
154                -1           GALAXY     0.4591        AMA  ...  921.870825   
204                -1           GALAXY     0.4591        MJO  ...  921.870825   
254                -1           GALAXY     0.4591        CHH  ...  921.870825   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
154        0.4591         GALAXY              2.0       2  0.0         0.4591   
204        0.4591         GALAXY              2.0       2  0.0         0.4591   
254        0.4591         GALAXY              2.0       2  0.0         0.4591   

                                       all VI comments  N_VI  \
154  unknown break at 9000 A|pipeline fit doesn't w...     3   
204  unknown break at 9000 A|pipeline fit doesn't w...     3   
254  unknown break at 9000 A|pipeline fit doesn't w...     3   

                                    merger comment  
154  Bad calibration. Possible absorption features  
204  Bad calibration. Possible absorption features  
254  Bad calibration. Possible absorption features  

[3 rows x 32 columns]

conflict ID =  20


In [63]:
#copy this text to a new cell to display the conflict
conflict_id=21
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
155  35191200679985679           GALAXY     1.3818        AMA           3   
205  35191200679985679           GALAXY     1.3818        MJO           4   
255  35191200679985679           GALAXY     1.3818        CHH           1   

    VI_issue    VI_z VI_spectype  \
155      NaN     NaN         NaN   
205        R  0.3525         NaN   
255        S     NaN         NaN   

                                            VI_comment  best redshift  \
155                                                 --         1.3818   
205  Ha + SII + OII + H&K + pipeline fit doesn't wo...         0.3525   
255  no emission or absorption lines; featureless c...         1.3818   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
155        GALAXY          2.666667        3         1.3818  0.761035   
205        GALAXY          2.666667        3         1.3818  0.761035   
255        GALAXY          2.666667        3         1.3818  0.761035   

                                       all VI comments  N_VI merger comment  
155  --|Ha + SII + OII + H&K + pipeline fit doesn't...     3           none  
205  --|Ha + SII + OII + H&K + pipeline fit doesn't...     3           none  
255  --|Ha + SII + OII + H&K + pipeline fit doesn't...     3           none

In [64]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.3525
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'flag disagreement. Redshift is secure. Bad calibration'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
155  35191200679985679  52932  20200303   70500       0.34.4               -1   
205  35191200679985679  52932  20200303   70500       0.34.4               -1   
255  35191200679985679  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
155                -1           GALAXY     1.3818        AMA  ...  125.076377   
205                -1           GALAXY     1.3818        MJO  ...  125.076377   
255                -1           GALAXY     1.3818        CHH  ...  125.076377   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
155        0.3525         GALAXY         2.666667       3  0.761035   
205        0.3525         GALAXY         2.666667       3  0.761035   
255        0.3525         GALAXY         2.666667       3  0.761035   

     vi_combined_z                                    all VI comments  N_VI  \
155         1.3818  --|Ha + SII + OII + H&K + pipeline fit doesn't...     3   
205         1.3818  --|Ha + SII + OII + H&K + pipeline fit doesn't...     3   
255         1.3818  --|Ha + SII + OII + H&K + pipeline fit doesn't...     3   

                                        merger comment  
155  flag disagreement. Redshift is secure. Bad cal...  
205  flag disagreement. Redshift is secure. Bad cal...  
255  flag disagreement. Redshift is secure. Bad cal...  

[3 rows x 32 columns]

conflict ID =  21


In [65]:
#copy this text to a new cell to display the conflict
conflict_id=22
display_conflict(conflict_id, show_spectra=show_spectra)



TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
157  35191200679986377           GALAXY     0.2857        AMA           3   
207  35191200679986377           GALAXY     0.2857        MJO           1   
257  35191200679986377           GALAXY     0.2857        CHH           1   

    VI_issue  VI_z VI_spectype  \
157      NaN   NaN         NaN   
207        R   NaN         NaN   
257      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
157                             possible O || emission         0.2857   
207  pipeline fit doesn't work well for the continu...         0.2857   
257     no emission or absorption lines; bad continuum         0.2857   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
157        GALAXY          1.666667        2         0.2857  0.0   
207        GALAXY          1.666667        2         0.2857  0.0   
257        GALAXY          1.666667        2         0.2857  0.0   

                                       all VI comments  N_VI merger comment  
157  possible O || emission|pipeline fit doesn't wo...     3           none  
207  possible O || emission|pipeline fit doesn't wo...     3           none  
257  possible O || emission|pipeline fit doesn't wo...     3           none

In [66]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. No features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
157  35191200679986377  52932  20200303   70500       0.34.4               -1   
207  35191200679986377  52932  20200303   70500       0.34.4               -1   
257  35191200679986377  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
157                -1           GALAXY     0.2857        AMA  ...  181.090337   
207                -1           GALAXY     0.2857        MJO  ...  181.090337   
257                -1           GALAXY     0.2857        CHH  ...  181.090337   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
157        0.2857         GALAXY         1.666667       2  0.0         0.2857   
207        0.2857         GALAXY         1.666667       2  0.0         0.2857   
257        0.2857         GALAXY         1.666667       2  0.0         0.2857   

                                       all VI comments  N_VI  \
157  possible O || emission|pipeline fit doesn't wo...     3   
207  possible O || emission|pipeline fit doesn't wo...     3   
257  possible O || emission|pipeline fit doesn't wo...     3   

                   merger comment  
157  Bad calibration. No features  
207  Bad calibration. No features  
257  Bad calibration. No features  

[3 rows x 32 columns]

conflict ID =  22


In [67]:
#copy this text to a new cell to display the conflict
conflict_id=23
display_conflict(conflict_id, show_spectra=show_spectra)



TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
158  35191200679986445           GALAXY     0.3146        AMA           3   
208  35191200679986445           GALAXY     0.3146        MJO           4   
258  35191200679986445           GALAXY     0.3146        CHH           1   

    VI_issue   VI_z VI_spectype  \
158      NaN    NaN         NaN   
208        R  0.247         NaN   
258      NaN    NaN         NaN   

                                            VI_comment  best redshift  \
158                                                 --         0.3146   
208  Ha + SII + OII + pipeline fit doesn't work wel...         0.2470   
258     no emission or absorption lines; bad continuum         0.3146   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z       dz  \
158        GALAXY          2.666667        3         0.3146  0.05421   
208        GALAXY          2.666667        3         0.3146  0.05421   
258        GALAXY          2.666667        3         0.3146  0.05421   

                                       all VI comments  N_VI merger comment  
158  --|Ha + SII + OII + pipeline fit doesn't work ...     3           none  
208  --|Ha + SII + OII + pipeline fit doesn't work ...     3           none  
258  --|Ha + SII + OII + pipeline fit doesn't work ...     3           none

In [68]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2370
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. Ha SII NII secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
158  35191200679986445  52932  20200303   70500       0.34.4               -1   
208  35191200679986445  52932  20200303   70500       0.34.4               -1   
258  35191200679986445  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
158                -1           GALAXY     0.3146        AMA  ...  171.306813   
208                -1           GALAXY     0.3146        MJO  ...  171.306813   
258                -1           GALAXY     0.3146        CHH  ...  171.306813   

    best redshift  best spectype vi_combined_flag vi_diff       dz  \
158         0.237         GALAXY         2.666667       3  0.05421   
208         0.237         GALAXY         2.666667       3  0.05421   
258         0.237         GALAXY         2.666667       3  0.05421   

     vi_combined_z                                    all VI comments  N_VI  \
158         0.3146  --|Ha + SII + OII + pipeline fit doesn't work ...     3   
208         0.3146  --|Ha + SII + OII + pipeline fit doesn't work ...     3   
258         0.3146  --|Ha + SII + OII + pipeline fit doesn't work ...     3   

                         merger comment  
158  Bad calibration. Ha SII NII secure  
208  Bad calibration. Ha SII NII secure  
258  Bad calibration. Ha SII NII secure  

[3 rows x 32 columns]

conflict ID =  23


In [69]:
#copy this text to a new cell to display the conflict
conflict_id=24
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
159  35191200679986644           GALAXY     1.1582        AMA           3   
209  35191200679986644           GALAXY     1.1582        MJO           4   
259  35191200679986644           GALAXY     1.1582        CHH           1   

    VI_issue    VI_z VI_spectype  \
159      NaN     NaN         NaN   
209        R  0.2263         NaN   
259        S     NaN         NaN   

                                            VI_comment  best redshift  \
159                                                 --         1.1582   
209  Ha + SII + OII + Hb + pipeline fit doesn't wor...         0.2263   
259     no emission or absorption lines; bad continuum         1.1582   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
159        GALAXY          2.666667        3         1.1582  0.759928   
209        GALAXY          2.666667        3         1.1582  0.759928   
259        GALAXY          2.666667        3         1.1582  0.759928   

                                       all VI comments  N_VI merger comment  
159  --|Ha + SII + OII + Hb + pipeline fit doesn't ...     3           none  
209  --|Ha + SII + OII + Hb + pipeline fit doesn't ...     3           none  
259  --|Ha + SII + OII + Hb + pipeline fit doesn't ...     3           none

In [70]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2263
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. Ha SII NII OIII OII secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
159  35191200679986644  52932  20200303   70500       0.34.4               -1   
209  35191200679986644  52932  20200303   70500       0.34.4               -1   
259  35191200679986644  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  \
159                -1           GALAXY     1.1582        AMA  ...   
209                -1           GALAXY     1.1582        MJO  ...   
259                -1           GALAXY     1.1582        CHH  ...   

       DELTACHI2 best redshift  best spectype vi_combined_flag vi_diff  \
159  1303.672758        0.2263         GALAXY         2.666667       3   
209  1303.672758        0.2263         GALAXY         2.666667       3   
259  1303.672758        0.2263         GALAXY         2.666667       3   

           dz  vi_combined_z  \
159  0.759928         1.1582   
209  0.759928         1.1582   
259  0.759928         1.1582   

                                       all VI comments  N_VI  \
159  --|Ha + SII + OII + Hb + pipeline fit doesn't ...     3   
209  --|Ha + SII + OII + Hb + pipeline fit doesn't ...     3   
259  --|Ha + SII + OII + Hb + pipeline fit doesn't ...     3   

                                  merger comment  
159  Bad calibration. Ha SII NII OIII OII secure  
209  Bad calibration. Ha SII NII OIII OII secure  
259  Bad calibration. Ha SII NII OIII OII secure  

[3 rows x 32 columns]

conflict ID =  24


In [71]:
#copy this text to a new cell to display the conflict
conflict_id=25
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
160  35191200679986752              QSO     1.1557        AMA           3   
210  35191200679986752              QSO     1.1557        MJO           1   
260  35191200679986752              QSO     1.1557        CHH           1   

    VI_issue    VI_z VI_spectype  \
160        R  1.0857         NaN   
210        R     NaN         NaN   
260        S     NaN         NaN   

                                            VI_comment  best redshift  \
160                                                 --         1.0857   
210  pipeline fit doesn't work well for the continu...         1.1557   
260     no emission or absorption lines; bad continuum         1.1557   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
160           QSO          1.666667        2         1.1557  0.033562   
210           QSO          1.666667        2         1.1557  0.033562   
260           QSO          1.666667        2         1.1557  0.033562   

                                       all VI comments  N_VI merger comment  
160  --|pipeline fit doesn't work well for the cont...     3           none  
210  --|pipeline fit doesn't work well for the cont...     3           none  
260  --|pipeline fit doesn't work well for the cont...     3           none

In [72]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2263
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. No obvious features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
160  35191200679986752  52932  20200303   70500       0.34.4               -1   
210  35191200679986752  52932  20200303   70500       0.34.4               -1   
260  35191200679986752  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
160                -1              QSO     1.1557        AMA  ...  106.077817   
210                -1              QSO     1.1557        MJO  ...  106.077817   
260                -1              QSO     1.1557        CHH  ...  106.077817   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
160        1.0857            QSO         1.666667       2  0.033562   
210        1.1557            QSO         1.666667       2  0.033562   
260        1.1557            QSO         1.666667       2  0.033562   

     vi_combined_z                                    all VI comments  N_VI  \
160         1.1557  --|pipeline fit doesn't work well for the cont...     3   
210         1.1557  --|pipeline fit doesn't work well for the cont...     3   
260         1.1557  --|pipeline fit doesn't work well for the cont...     3   

                           merger comment  
160  Bad calibration. No obvious features  
210  Bad calibration. No obvious features  
260  Bad calibration. No obvious features  

[3 rows x 32 columns]

conflict ID =  25


In [73]:
#copy this text to a new cell to display the conflict
conflict_id=26
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
163  35191200679988159              QSO     1.1499        AMA           2   
213  35191200679988159              QSO     1.1499        MJO           4   
263  35191200679988159              QSO     1.1499        CHH           1   

    VI_issue    VI_z VI_spectype  \
163      NaN  1.0899         NaN   
213       RC  0.2699      GALAXY   
263        S     NaN         NaN   

                                            VI_comment  best redshift  \
163                                                 --         1.0899   
213  H&K + G + Hb + MgI + D + pipeline fit doesn't ...         0.2699   
263     no emission or absorption lines; bad continuum         1.1499   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
163           QSO          2.333333        3         1.1499  0.692968   
213        GALAXY          2.333333        3         1.1499  0.692968   
263           QSO          2.333333        3         1.1499  0.692968   

                                       all VI comments  N_VI merger comment  
163  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3           none  
213  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3           none  
263  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3           none

In [74]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2699
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. absorption  features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
163  35191200679988159  52932  20200303   70500       0.34.4               -1   
213  35191200679988159  52932  20200303   70500       0.34.4               -1   
263  35191200679988159  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
163                -1              QSO     1.1499        AMA  ...  44.535669   
213                -1              QSO     1.1499        MJO  ...  44.535669   
263                -1              QSO     1.1499        CHH  ...  44.535669   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
163        0.2699            QSO         2.333333       3  0.692968   
213        0.2699         GALAXY         2.333333       3  0.692968   
263        0.2699            QSO         2.333333       3  0.692968   

     vi_combined_z                                    all VI comments  N_VI  \
163         1.1499  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   
213         1.1499  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   
263         1.1499  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   

                                       merger comment  
163  Bad calibration. absorption  features are secure  
213  Bad calibration. absorption  features are secure  
263  Bad calibration. absorption  features are secure  

[3 rows x 32 columns]

conflict ID =  26


In [75]:
#copy this text to a new cell to display the conflict
conflict_id=27
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
164  35191200679988196           GALAXY     0.4266        AMA           3   
214  35191200679988196           GALAXY     0.4266        MJO           4   
264  35191200679988196           GALAXY     0.4266        CHH           1   

    VI_issue  VI_z VI_spectype  \
164      NaN   NaN         NaN   
214        R   NaN         NaN   
264      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
164                                                 --         0.4266   
214  Ha + H&K + Hd + G + MgI + D + pipeline fit doe...         0.4266   
264  no emission or absorption lines; featureless c...         0.4266   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
164        GALAXY          2.666667        3         0.4266  0.0   
214        GALAXY          2.666667        3         0.4266  0.0   
264        GALAXY          2.666667        3         0.4266  0.0   

                                       all VI comments  N_VI merger comment  
164  --|Ha + H&K + Hd + G + MgI + D + pipeline fit ...     3           none  
214  --|Ha + H&K + Hd + G + MgI + D + pipeline fit ...     3           none  
264  --|Ha + H&K + Hd + G + MgI + D + pipeline fit ...     3           none

In [76]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2699
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. Possible Ha. Be conservative'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
164  35191200679988196  52932  20200303   70500       0.34.4               -1   
214  35191200679988196  52932  20200303   70500       0.34.4               -1   
264  35191200679988196  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
164                -1           GALAXY     0.4266        AMA  ...  163.526345   
214                -1           GALAXY     0.4266        MJO  ...  163.526345   
264                -1           GALAXY     0.4266        CHH  ...  163.526345   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
164        0.4266         GALAXY         2.666667       3  0.0         0.4266   
214        0.4266         GALAXY         2.666667       3  0.0         0.4266   
264        0.4266         GALAXY         2.666667       3  0.0         0.4266   

                                       all VI comments  N_VI  \
164  --|Ha + H&K + Hd + G + MgI + D + pipeline fit ...     3   
214  --|Ha + H&K + Hd + G + MgI + D + pipeline fit ...     3   
264  --|Ha + H&K + Hd + G + MgI + D + pipeline fit ...     3   

                                    merger comment  
164  Bad calibration. Possible Ha. Be conservative  
214  Bad calibration. Possible Ha. Be conservative  
264  Bad calibration. Possible Ha. Be conservative  

[3 rows x 32 columns]

conflict ID =  27


In [77]:
#copy this text to a new cell to display the conflict
conflict_id=28
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
173  35191204660380487           GALAXY     0.3468        AMA          -1   
223  35191204660380487           GALAXY     0.3468        MJO           4   
273  35191204660380487           GALAXY     0.3468        CHH           3   

    VI_issue  VI_z VI_spectype                             VI_comment  \
173      NaN   NaN         NaN     no strong features; weak continuum   
223      NaN   NaN         NaN                     OII H&K G Hb MgI D   
273      NaN   NaN         NaN  H; K; Mg; D absorption; bad continuum   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
173         0.3468        GALAXY               2.0        5         0.3468   
223         0.3468        GALAXY               2.0        5         0.3468   
273         0.3468        GALAXY               2.0        5         0.3468   

      dz                                    all VI comments  N_VI  \
173  0.0  no strong features; weak continuum|OII H&K G H...     3   
223  0.0  no strong features; weak continuum|OII H&K G H...     3   
273  0.0  no strong features; weak continuum|OII H&K G H...     3   

    merger comment  
173           none  
223           none  
273           none

In [78]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2699
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. absorption features are robust'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
173  35191204660380487  52932  20200303   70500       0.34.4               -1   
223  35191204660380487  52932  20200303   70500       0.34.4               -1   
273  35191204660380487  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
173                -1           GALAXY     0.3468        AMA  ...    680.296   
223                -1           GALAXY     0.3468        MJO  ...    680.296   
273                -1           GALAXY     0.3468        CHH  ...    680.296   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
173        0.3468         GALAXY              2.0       5  0.0         0.3468   
223        0.3468         GALAXY              2.0       5  0.0         0.3468   
273        0.3468         GALAXY              2.0       5  0.0         0.3468   

                                       all VI comments  N_VI  \
173  no strong features; weak continuum|OII H&K G H...     3   
223  no strong features; weak continuum|OII H&K G H...     3   
273  no strong features; weak continuum|OII H&K G H...     3   

                                      merger comment  
173  Bad calibration. absorption features are robust  
223  Bad calibration. absorption features are robust  
273  Bad calibration. absorption features are robust  

[3 rows x 32 columns]

conflict ID =  28


In [79]:
#copy this text to a new cell to display the conflict
conflict_id=29
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
174  35191204660381031           GALAXY     0.3177        AMA           2   
224  35191204660381031           GALAXY     0.3177        MJO           1   
274  35191204660381031           GALAXY     0.3177        CHH           3   

    VI_issue  VI_z VI_spectype                                  VI_comment  \
174      NaN   NaN         NaN          no strong features; weak continuum   
224      NaN   NaN         NaN                       not sure what this is   
274      NaN   NaN         NaN  weak H; K; Mg; D absorption; bad continuum   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
174         0.3177        GALAXY               2.0        2         0.3177   
224         0.3177        GALAXY               2.0        2         0.3177   
274         0.3177        GALAXY               2.0        2         0.3177   

      dz                                    all VI comments  N_VI  \
174  0.0  no strong features; weak continuum|not sure wh...     3   
224  0.0  no strong features; weak continuum|not sure wh...     3   
274  0.0  no strong features; weak continuum|not sure wh...     3   

    merger comment  
174           none  
224           none  
274           none

In [80]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2699
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. absorption features are not secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
174  35191204660381031  52932  20200303   70500       0.34.4               -1   
224  35191204660381031  52932  20200303   70500       0.34.4               -1   
274  35191204660381031  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
174                -1           GALAXY     0.3177        AMA  ...  221.699107   
224                -1           GALAXY     0.3177        MJO  ...  221.699107   
274                -1           GALAXY     0.3177        CHH  ...  221.699107   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
174        0.3177         GALAXY              2.0       2  0.0         0.3177   
224        0.3177         GALAXY              2.0       2  0.0         0.3177   
274        0.3177         GALAXY              2.0       2  0.0         0.3177   

                                       all VI comments  N_VI  \
174  no strong features; weak continuum|not sure wh...     3   
224  no strong features; weak continuum|not sure wh...     3   
274  no strong features; weak continuum|not sure wh...     3   

                                        merger comment  
174  Bad calibration. absorption features are not s...  
224  Bad calibration. absorption features are not s...  
274  Bad calibration. absorption features are not s...  

[3 rows x 32 columns]

conflict ID =  29


In [81]:
#copy this text to a new cell to display the conflict
conflict_id=30
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
180  35191204664574094           GALAXY     0.3758        AMA           2   
230  35191204664574094           GALAXY     0.3758        MJO           4   
280  35191204664574094           GALAXY     0.3758        CHH           1   

    VI_issue  VI_z VI_spectype  \
180      NaN   NaN         NaN   
230      NaN   NaN         NaN   
280      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
180                                 no strong features         0.3758   
230                                 H&K + Hb + MgI + D         0.3758   
280  no emission or absorption lines; featureless c...         0.3758   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
180        GALAXY          2.333333        3         0.3758  0.0   
230        GALAXY          2.333333        3         0.3758  0.0   
280        GALAXY          2.333333        3         0.3758  0.0   

                                       all VI comments  N_VI merger comment  
180  no strong features|H&K + Hb + MgI + D|no emiss...     3           none  
230  no strong features|H&K + Hb + MgI + D|no emiss...     3           none  
280  no strong features|H&K + Hb + MgI + D|no emiss...     3           none

In [82]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2699
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. absorption features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
180  35191204664574094  52932  20200303   70500       0.34.4               -1   
230  35191204664574094  52932  20200303   70500       0.34.4               -1   
280  35191204664574094  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
180                -1           GALAXY     0.3758        AMA  ...  854.493748   
230                -1           GALAXY     0.3758        MJO  ...  854.493748   
280                -1           GALAXY     0.3758        CHH  ...  854.493748   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
180        0.3758         GALAXY         2.333333       3  0.0         0.3758   
230        0.3758         GALAXY         2.333333       3  0.0         0.3758   
280        0.3758         GALAXY         2.333333       3  0.0         0.3758   

                                       all VI comments  N_VI  \
180  no strong features|H&K + Hb + MgI + D|no emiss...     3   
230  no strong features|H&K + Hb + MgI + D|no emiss...     3   
280  no strong features|H&K + Hb + MgI + D|no emiss...     3   

                                      merger comment  
180  Bad calibration. absorption features are secure  
230  Bad calibration. absorption features are secure  
280  Bad calibration. absorption features are secure  

[3 rows x 32 columns]

conflict ID =  30


In [83]:
#copy this text to a new cell to display the conflict
conflict_id=31
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
182  35191204664575007           GALAXY     0.3863        AMA           2   
232  35191204664575007           GALAXY     0.3863        MJO           3   
282  35191204664575007           GALAXY     0.3863        CHH           1   

    VI_issue  VI_z VI_spectype  \
182      NaN   NaN         NaN   
232      NaN   NaN         NaN   
282      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
182                                 no strong features         0.3863   
232                            Ha + some week features         0.3863   
282  no emission or absorption lines; featureless c...         0.3863   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
182        GALAXY               2.0        2         0.3863  0.0   
232        GALAXY               2.0        2         0.3863  0.0   
282        GALAXY               2.0        2         0.3863  0.0   

                                       all VI comments  N_VI merger comment  
182  no strong features|Ha + some week features|no ...     3           none  
232  no strong features|Ha + some week features|no ...     3           none  
282  no strong features|Ha + some week features|no ...     3           none

In [84]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2699
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. emission and absorption features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
182  35191204664575007  52932  20200303   70500       0.34.4               -1   
232  35191204664575007  52932  20200303   70500       0.34.4               -1   
282  35191204664575007  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
182                -1           GALAXY     0.3863        AMA  ...  896.660985   
232                -1           GALAXY     0.3863        MJO  ...  896.660985   
282                -1           GALAXY     0.3863        CHH  ...  896.660985   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
182        0.3863         GALAXY              2.0       2  0.0         0.3863   
232        0.3863         GALAXY              2.0       2  0.0         0.3863   
282        0.3863         GALAXY              2.0       2  0.0         0.3863   

                                       all VI comments  N_VI  \
182  no strong features|Ha + some week features|no ...     3   
232  no strong features|Ha + some week features|no ...     3   
282  no strong features|Ha + some week features|no ...     3   

                                        merger comment  
182  Bad calibration. emission and absorption featu...  
232  Bad calibration. emission and absorption featu...  
282  Bad calibration. emission and absorption featu...  

[3 rows x 32 columns]

conflict ID =  31


In [85]:
#copy this text to a new cell to display the conflict
conflict_id=32
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
185  35191204664576079           GALAXY     0.4182        AMA           2   
235  35191204664576079           GALAXY     0.4182        MJO           4   
285  35191204664576079           GALAXY     0.4182        CHH           1   

    VI_issue    VI_z VI_spectype  \
185        R  0.3842         NaN   
235        R  0.5224         NaN   
285        S     NaN         NaN   

                                         VI_comment  best redshift  \
185                        possible redshift misfit         0.3842   
235                           OII + H&K + Hb + OIII         0.5224   
285  no emission or absorption lines; bad continuum         0.4182   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
185        GALAXY          2.333333        3         0.4182  0.099841   
235        GALAXY          2.333333        3         0.4182  0.099841   
285        GALAXY          2.333333        3         0.4182  0.099841   

                                       all VI comments  N_VI merger comment  
185  possible redshift misfit|OII + H&K + Hb + OIII...     3           none  
235  possible redshift misfit|OII + H&K + Hb + OIII...     3           none  
285  possible redshift misfit|OII + H&K + Hb + OIII...     3           none

In [86]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.5224
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. emission features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
185  35191204664576079  52932  20200303   70500       0.34.4               -1   
235  35191204664576079  52932  20200303   70500       0.34.4               -1   
285  35191204664576079  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
185                -1           GALAXY     0.4182        AMA  ...  92.287746   
235                -1           GALAXY     0.4182        MJO  ...  92.287746   
285                -1           GALAXY     0.4182        CHH  ...  92.287746   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
185        0.5224         GALAXY         2.333333       3  0.099841   
235        0.5224         GALAXY         2.333333       3  0.099841   
285        0.5224         GALAXY         2.333333       3  0.099841   

     vi_combined_z                                    all VI comments  N_VI  \
185         0.4182  possible redshift misfit|OII + H&K + Hb + OIII...     3   
235         0.4182  possible redshift misfit|OII + H&K + Hb + OIII...     3   
285         0.4182  possible redshift misfit|OII + H&K + Hb + OIII...     3   

                                    merger comment  
185  Bad calibration. emission features are secure  
235  Bad calibration. emission features are secure  
285  Bad calibration. emission features are secure  

[3 rows x 32 columns]

conflict ID =  32


In [87]:
#copy this text to a new cell to display the conflict
conflict_id=33
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
188  35191204668769563           GALAXY     0.3785        AMA           3   
238  35191204668769563           GALAXY     0.3785        MJO           1   
288  35191204668769563           GALAXY     0.3785        CHH           1   

    VI_issue    VI_z VI_spectype  \
188      NaN     NaN         NaN   
238      NaN  0.6826         NaN   
288      NaN     NaN         NaN   

                                            VI_comment  best redshift  \
188                                                 --         0.3785   
238                                                 --         0.6826   
288  no emission or absorption lines; featureless c...         0.3785   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
188        GALAXY          1.666667        2         0.3785  0.220602   
238        GALAXY          1.666667        2         0.3785  0.220602   
288        GALAXY          1.666667        2         0.3785  0.220602   

                                       all VI comments  N_VI merger comment  
188  --|--|no emission or absorption lines; feature...     3           none  
238  --|--|no emission or absorption lines; feature...     3           none  
288  --|--|no emission or absorption lines; feature...     3           none

In [88]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.5224
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. No features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
188  35191204668769563  52932  20200303   70500       0.34.4               -1   
238  35191204668769563  52932  20200303   70500       0.34.4               -1   
288  35191204668769563  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
188                -1           GALAXY     0.3785        AMA  ...  20.109048   
238                -1           GALAXY     0.3785        MJO  ...  20.109048   
288                -1           GALAXY     0.3785        CHH  ...  20.109048   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
188        0.3785         GALAXY         1.666667       2  0.220602   
238        0.6826         GALAXY         1.666667       2  0.220602   
288        0.3785         GALAXY         1.666667       2  0.220602   

     vi_combined_z                                    all VI comments  N_VI  \
188         0.3785  --|--|no emission or absorption lines; feature...     3   
238         0.3785  --|--|no emission or absorption lines; feature...     3   
288         0.3785  --|--|no emission or absorption lines; feature...     3   

                   merger comment  
188  Bad calibration. No features  
238  Bad calibration. No features  
288  Bad calibration. No features  

[3 rows x 32 columns]

conflict ID =  33


In [89]:
#copy this text to a new cell to display the conflict
conflict_id=34
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
190  35191204668771151           GALAXY     0.3366        AMA           4   
240  35191204668771151           GALAXY     0.3366        MJO           4   
290  35191204668771151           GALAXY     0.3366        CHH           1   

    VI_issue  VI_z VI_spectype  \
190      NaN   NaN         NaN   
240      NaN   NaN         NaN   
290      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
190                                                 --         0.3366   
240                                 H&K + MgI + D + Ha         0.3366   
290  no emission or absorption lines; featureless c...         0.3366   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
190        GALAXY               3.0        3         0.3366  0.0   
240        GALAXY               3.0        3         0.3366  0.0   
290        GALAXY               3.0        3         0.3366  0.0   

                                       all VI comments  N_VI merger comment  
190  --|H&K + MgI + D + Ha|no emission or absorptio...     3           none  
240  --|H&K + MgI + D + Ha|no emission or absorptio...     3           none  
290  --|H&K + MgI + D + Ha|no emission or absorptio...     3           none

In [90]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.5224
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. emission and absorption features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
190  35191204668771151  52932  20200303   70500       0.34.4               -1   
240  35191204668771151  52932  20200303   70500       0.34.4               -1   
290  35191204668771151  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
190                -1           GALAXY     0.3366        AMA  ...  505.666622   
240                -1           GALAXY     0.3366        MJO  ...  505.666622   
290                -1           GALAXY     0.3366        CHH  ...  505.666622   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
190        0.3366         GALAXY              3.0       3  0.0         0.3366   
240        0.3366         GALAXY              3.0       3  0.0         0.3366   
290        0.3366         GALAXY              3.0       3  0.0         0.3366   

                                       all VI comments  N_VI  \
190  --|H&K + MgI + D + Ha|no emission or absorptio...     3   
240  --|H&K + MgI + D + Ha|no emission or absorptio...     3   
290  --|H&K + MgI + D + Ha|no emission or absorptio...     3   

                                        merger comment  
190  Bad calibration. emission and absorption featu...  
240  Bad calibration. emission and absorption featu...  
290  Bad calibration. emission and absorption featu...  

[3 rows x 32 columns]

conflict ID =  34


In [91]:
#copy this text to a new cell to display the conflict
conflict_id=35
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
191  35191204668772416           GALAXY     0.4797        AMA           4   
241  35191204668772416           GALAXY     0.4797        MJO           3   
291  35191204668772416           GALAXY     0.4797        CHH           2   

    VI_issue  VI_z VI_spectype  \
191      NaN   NaN         NaN   
241        R   NaN         NaN   
291      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
191                                                 --         0.4797   
241  pipeline fit doesn't work well for the continu...         0.4797   
291            possible H; K absorption; bad continuum         0.4797   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
191        GALAXY               3.0        2         0.4797  0.0   
241        GALAXY               3.0        2         0.4797  0.0   
291        GALAXY               3.0        2         0.4797  0.0   

                                       all VI comments  N_VI merger comment  
191  --|pipeline fit doesn't work well for the cont...     3           none  
241  --|pipeline fit doesn't work well for the cont...     3           none  
291  --|pipeline fit doesn't work well for the cont...     3           none

In [92]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.5224
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration.absorption features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
191  35191204668772416  52932  20200303   70500       0.34.4               -1   
241  35191204668772416  52932  20200303   70500       0.34.4               -1   
291  35191204668772416  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
191                -1           GALAXY     0.4797        AMA  ...  335.432626   
241                -1           GALAXY     0.4797        MJO  ...  335.432626   
291                -1           GALAXY     0.4797        CHH  ...  335.432626   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
191        0.4797         GALAXY              3.0       2  0.0         0.4797   
241        0.4797         GALAXY              3.0       2  0.0         0.4797   
291        0.4797         GALAXY              3.0       2  0.0         0.4797   

                                       all VI comments  N_VI  \
191  --|pipeline fit doesn't work well for the cont...     3   
241  --|pipeline fit doesn't work well for the cont...     3   
291  --|pipeline fit doesn't work well for the cont...     3   

                                     merger comment  
191  Bad calibration.absorption features are secure  
241  Bad calibration.absorption features are secure  
291  Bad calibration.absorption features are secure  

[3 rows x 32 columns]

conflict ID =  35


In [93]:
#copy this text to a new cell to display the conflict
conflict_id=36
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
197  35191208632387461           GALAXY     0.2607        AMA           2   
247  35191208632387461           GALAXY     0.2607        MJO           4   
297  35191208632387461           GALAXY     0.2607        CHH           4   

    VI_issue  VI_z VI_spectype                                   VI_comment  \
197      NaN   NaN         NaN                           no strong features   
247      NaN   NaN         NaN                                  H&K G MgI D   
297      NaN   NaN         NaN  H; K; Hbeta; MgI; D absoprtion; 4000A break   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
197         0.2607        GALAXY          3.333333        2         0.2607   
247         0.2607        GALAXY          3.333333        2         0.2607   
297         0.2607        GALAXY          3.333333        2         0.2607   

      dz                                    all VI comments  N_VI  \
197  0.0  no strong features|H&K G MgI D|H; K; Hbeta; Mg...     3   
247  0.0  no strong features|H&K G MgI D|H; K; Hbeta; Mg...     3   
297  0.0  no strong features|H&K G MgI D|H; K; Hbeta; Mg...     3   

    merger comment  
197           none  
247           none  
297           none

In [94]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.5224
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'absorption features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
197  35191208632387461  52932  20200303   70500       0.34.4               -1   
247  35191208632387461  52932  20200303   70500       0.34.4               -1   
297  35191208632387461  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  \
197                -1           GALAXY     0.2607        AMA  ...   
247                -1           GALAXY     0.2607        MJO  ...   
297                -1           GALAXY     0.2607        CHH  ...   

       DELTACHI2 best redshift  best spectype vi_combined_flag vi_diff   dz  \
197  1713.431124        0.2607         GALAXY         3.333333       2  0.0   
247  1713.431124        0.2607         GALAXY         3.333333       2  0.0   
297  1713.431124        0.2607         GALAXY         3.333333       2  0.0   

     vi_combined_z                                    all VI comments  N_VI  \
197         0.2607  no strong features|H&K G MgI D|H; K; Hbeta; Mg...     3   
247         0.2607  no strong features|H&K G MgI D|H; K; Hbeta; Mg...     3   
297         0.2607  no strong features|H&K G MgI D|H; K; Hbeta; Mg...     3   

                     merger comment  
197  absorption features are secure  
247  absorption features are secure  
297  absorption features are secure  

[3 rows x 32 columns]

conflict ID =  36


In [95]:
#copy this text to a new cell to display the conflict
conflict_id=37
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
199  35191208632388250           GALAXY     0.4719        AMA           4   
249  35191208632388250           GALAXY     0.4719        MJO           4   
299  35191208632388250           GALAXY     0.4719        CHH           2   

    VI_issue  VI_z VI_spectype                                  VI_comment  \
199      NaN   NaN         NaN                                          --   
249      NaN   NaN         NaN                                          --   
299      NaN   NaN         NaN  possible OII Hbeta emission; bad continuum   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
199         0.4719        GALAXY          3.333333        2         0.4719   
249         0.4719        GALAXY          3.333333        2         0.4719   
299         0.4719        GALAXY          3.333333        2         0.4719   

      dz                                   all VI comments  N_VI  \
199  0.0  --|--|possible OII Hbeta emission; bad continuum     3   
249  0.0  --|--|possible OII Hbeta emission; bad continuum     3   
299  0.0  --|--|possible OII Hbeta emission; bad continuum     3   

    merger comment  
199           none  
249           none  
299           none

In [96]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.5224
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
199  35191208632388250  52932  20200303   70500       0.34.4               -1   
249  35191208632388250  52932  20200303   70500       0.34.4               -1   
299  35191208632388250  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  \
199                -1           GALAXY     0.4719        AMA  ...   
249                -1           GALAXY     0.4719        MJO  ...   
299                -1           GALAXY     0.4719        CHH  ...   

       DELTACHI2 best redshift  best spectype vi_combined_flag vi_diff   dz  \
199  3030.979683        0.4719         GALAXY         3.333333       2  0.0   
249  3030.979683        0.4719         GALAXY         3.333333       2  0.0   
299  3030.979683        0.4719         GALAXY         3.333333       2  0.0   

     vi_combined_z                                   all VI comments  N_VI  \
199         0.4719  --|--|possible OII Hbeta emission; bad continuum     3   
249         0.4719  --|--|possible OII Hbeta emission; bad continuum     3   
299         0.4719  --|--|possible OII Hbeta emission; bad continuum     3   

                           merger comment  
199  Bad calibration. features are secure  
249  Bad calibration. features are secure  
299  Bad calibration. features are secure  

[3 rows x 32 columns]

conflict ID =  37


In [97]:
#copy this text to a new cell to display the conflict
conflict_id=38
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
301  35191208632389009           GALAXY     1.1186        CHH           1   
351  35191208632389009           GALAXY     1.1186        MJO           4   
401  35191208632389009           GALAXY     1.1186        AMA           3   

    VI_issue   VI_z VI_spectype  \
301      NaN    NaN         NaN   
351        R  0.213         NaN   
401      NaN    NaN         NaN   

                                            VI_comment  best redshift  \
301  No clear emission or absorption lines; bad con...         1.1186   
351                                     Ha + SII + OII         0.2130   
401                                                 --         1.1186   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
301        GALAXY          2.666667        3         1.1186  0.746579   
351        GALAXY          2.666667        3         1.1186  0.746579   
401        GALAXY          2.666667        3         1.1186  0.746579   

                                       all VI comments  N_VI merger comment  
301  No clear emission or absorption lines; bad con...     3           none  
351  No clear emission or absorption lines; bad con...     3           none  
401  No clear emission or absorption lines; bad con...     3           none

In [98]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. emission features are secure'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
301  35191208632389009  52932  20200303   70500       0.34.4               -1   
351  35191208632389009  52932  20200303   70500       0.34.4               -1   
401  35191208632389009  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
301                -1           GALAXY     1.1186        CHH  ...  641.301949   
351                -1           GALAXY     1.1186        MJO  ...  641.301949   
401                -1           GALAXY     1.1186        AMA  ...  641.301949   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
301         0.203         GALAXY         2.666667       3  0.746579   
351         0.203         GALAXY         2.666667       3  0.746579   
401         0.203         GALAXY         2.666667       3  0.746579   

     vi_combined_z                                    all VI comments  N_VI  \
301         1.1186  No clear emission or absorption lines; bad con...     3   
351         1.1186  No clear emission or absorption lines; bad con...     3   
401         1.1186  No clear emission or absorption lines; bad con...     3   

                                    merger comment  
301  Bad calibration. emission features are secure  
351  Bad calibration. emission features are secure  
401  Bad calibration. emission features are secure  

[3 rows x 32 columns]

conflict ID =  38


In [99]:
#copy this text to a new cell to display the conflict
conflict_id=39
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
307  35191208636583994           GALAXY     0.3042        CHH           1   
357  35191208636583994           GALAXY     0.3042        MJO           1   
407  35191208636583994           GALAXY     0.3042        AMA           3   

    VI_issue  VI_z VI_spectype  \
307      NaN   NaN         NaN   
357        R   NaN         NaN   
407      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
307  no emission or absorption lines; bad continuum...         0.3042   
357                              not sure what this is         0.3042   
407                                                 --         0.3042   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
307        GALAXY          1.666667        2         0.3042  0.0   
357        GALAXY          1.666667        2         0.3042  0.0   
407        GALAXY          1.666667        2         0.3042  0.0   

                                       all VI comments  N_VI merger comment  
307  no emission or absorption lines; bad continuum...     3           none  
357  no emission or absorption lines; bad continuum...     3           none  
407  no emission or absorption lines; bad continuum...     3           none

In [100]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. no secure features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
307  35191208636583994  52932  20200303   70500       0.34.4               -1   
357  35191208636583994  52932  20200303   70500       0.34.4               -1   
407  35191208636583994  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
307                -1           GALAXY     0.3042        CHH  ...   36.55018   
357                -1           GALAXY     0.3042        MJO  ...   36.55018   
407                -1           GALAXY     0.3042        AMA  ...   36.55018   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
307        0.3042         GALAXY         1.666667       2  0.0         0.3042   
357        0.3042         GALAXY         1.666667       2  0.0         0.3042   
407        0.3042         GALAXY         1.666667       2  0.0         0.3042   

                                       all VI comments  N_VI  \
307  no emission or absorption lines; bad continuum...     3   
357  no emission or absorption lines; bad continuum...     3   
407  no emission or absorption lines; bad continuum...     3   

                          merger comment  
307  Bad calibration. no secure features  
357  Bad calibration. no secure features  
407  Bad calibration. no secure features  

[3 rows x 32 columns]

conflict ID =  39


In [101]:
#copy this text to a new cell to display the conflict
conflict_id=40
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
308  35191212583422687           GALAXY     0.2968        CHH           1   
358  35191212583422687           GALAXY     0.2968        MJO           2   
408  35191212583422687           GALAXY     0.2968        AMA           3   

    VI_issue    VI_z VI_spectype  \
308      NaN     NaN         NaN   
358      NaN  0.1980         NaN   
408        R  0.3168         NaN   

                                            VI_comment  best redshift  \
308  no emission or absorption lines; bad continuum...         0.2968   
358                                    (H&K +) MgI + D         0.1980   
408                        possible incorrect redshift         0.3168   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
308        GALAXY               2.0        2         0.2968  0.099165   
358        GALAXY               2.0        2         0.2968  0.099165   
408        GALAXY               2.0        2         0.2968  0.099165   

                                       all VI comments  N_VI merger comment  
308  no emission or absorption lines; bad continuum...     3           none  
358  no emission or absorption lines; bad continuum...     3           none  
408  no emission or absorption lines; bad continuum...     3           none

In [102]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. no secure features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
308  35191212583422687  52932  20200303   70500       0.34.4               -1   
358  35191212583422687  52932  20200303   70500       0.34.4               -1   
408  35191212583422687  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
308                -1           GALAXY     0.2968        CHH  ...  180.039174   
358                -1           GALAXY     0.2968        MJO  ...  180.039174   
408                -1           GALAXY     0.2968        AMA  ...  180.039174   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
308        0.2968         GALAXY              2.0       2  0.099165   
358        0.1980         GALAXY              2.0       2  0.099165   
408        0.3168         GALAXY              2.0       2  0.099165   

     vi_combined_z                                    all VI comments  N_VI  \
308         0.2968  no emission or absorption lines; bad continuum...     3   
358         0.2968  no emission or absorption lines; bad continuum...     3   
408         0.2968  no emission or absorption lines; bad continuum...     3   

                          merger comment  
308  Bad calibration. no secure features  
358  Bad calibration. no secure features  
408  Bad calibration. no secure features  

[3 rows x 32 columns]

conflict ID =  40


In [103]:
#copy this text to a new cell to display the conflict
conflict_id=41
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
309  35191212583422940           GALAXY     0.3144        CHH           1   
359  35191212583422940           GALAXY     0.3144        MJO           1   
409  35191212583422940           GALAXY     0.3144        AMA           3   

    VI_issue  VI_z VI_spectype  \
309      NaN   NaN         NaN   
359      NaN   NaN         NaN   
409      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
309  no emission or absorption lines; bad continuum...         0.3144   
359                               no idea what this is         0.3144   
409                                                 --         0.3144   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
309        GALAXY          1.666667        2         0.3144  0.0   
359        GALAXY          1.666667        2         0.3144  0.0   
409        GALAXY          1.666667        2         0.3144  0.0   

                                       all VI comments  N_VI merger comment  
309  no emission or absorption lines; bad continuum...     3           none  
359  no emission or absorption lines; bad continuum...     3           none  
409  no emission or absorption lines; bad continuum...     3           none

In [104]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. no secure features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
309  35191212583422940  52932  20200303   70500       0.34.4               -1   
359  35191212583422940  52932  20200303   70500       0.34.4               -1   
409  35191212583422940  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
309                -1           GALAXY     0.3144        CHH  ...  131.575446   
359                -1           GALAXY     0.3144        MJO  ...  131.575446   
409                -1           GALAXY     0.3144        AMA  ...  131.575446   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
309        0.3144         GALAXY         1.666667       2  0.0         0.3144   
359        0.3144         GALAXY         1.666667       2  0.0         0.3144   
409        0.3144         GALAXY         1.666667       2  0.0         0.3144   

                                       all VI comments  N_VI  \
309  no emission or absorption lines; bad continuum...     3   
359  no emission or absorption lines; bad continuum...     3   
409  no emission or absorption lines; bad continuum...     3   

                          merger comment  
309  Bad calibration. no secure features  
359  Bad calibration. no secure features  
409  Bad calibration. no secure features  

[3 rows x 32 columns]

conflict ID =  41


In [105]:
#copy this text to a new cell to display the conflict
conflict_id=42
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
310  35191212583423743           GALAXY     0.2886        CHH           1   
360  35191212583423743           GALAXY     0.2886        MJO           1   
410  35191212583423743           GALAXY     0.2886        AMA           3   

    VI_issue  VI_z VI_spectype  \
310      NaN   NaN         NaN   
360      NaN   NaN         NaN   
410      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
310  no emission or absorption line features; bad c...         0.2886   
360                               no idea what this is         0.2886   
410                                                 --         0.2886   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
310        GALAXY          1.666667        2         0.2886  0.0   
360        GALAXY          1.666667        2         0.2886  0.0   
410        GALAXY          1.666667        2         0.2886  0.0   

                                       all VI comments  N_VI merger comment  
310  no emission or absorption line features; bad c...     3           none  
360  no emission or absorption line features; bad c...     3           none  
410  no emission or absorption line features; bad c...     3           none

In [106]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. no secure features'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
310  35191212583423743  52932  20200303   70500       0.34.4               -1   
360  35191212583423743  52932  20200303   70500       0.34.4               -1   
410  35191212583423743  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
310                -1           GALAXY     0.2886        CHH  ...  66.784335   
360                -1           GALAXY     0.2886        MJO  ...  66.784335   
410                -1           GALAXY     0.2886        AMA  ...  66.784335   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
310        0.2886         GALAXY         1.666667       2  0.0         0.2886   
360        0.2886         GALAXY         1.666667       2  0.0         0.2886   
410        0.2886         GALAXY         1.666667       2  0.0         0.2886   

                                       all VI comments  N_VI  \
310  no emission or absorption line features; bad c...     3   
360  no emission or absorption line features; bad c...     3   
410  no emission or absorption line features; bad c...     3   

                          merger comment  
310  Bad calibration. no secure features  
360  Bad calibration. no secure features  
410  Bad calibration. no secure features  

[3 rows x 32 columns]

conflict ID =  42


In [107]:
#copy this text to a new cell to display the conflict
conflict_id=43
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
316  35191212587616712           GALAXY     0.0904        CHH           2   
366  35191212587616712           GALAXY     0.0904        MJO           3   
416  35191212587616712           GALAXY     0.0904        AMA           1   

    VI_issue  VI_z VI_spectype          VI_comment  best redshift  \
316      NaN   NaN         NaN    On emission line         0.0904   
366      NaN   NaN         NaN  Ha (+ SII) + Ca II         0.0904   
416        C   NaN         QSO        Possible QSO         0.0904   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
316        GALAXY               2.0        2         0.0904  0.0   
366        GALAXY               2.0        2         0.0904  0.0   
416           QSO               2.0        2         0.0904  0.0   

                                      all VI comments  N_VI merger comment  
316  On emission line|Ha (+ SII) + Ca II|Possible QSO     3           none  
366  On emission line|Ha (+ SII) + Ca II|Possible QSO     3           none  
416  On emission line|Ha (+ SII) + Ca II|Possible QSO     3           none

In [108]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. Secure emission'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
316  35191212587616712  52932  20200303   70500       0.34.4               -1   
366  35191212587616712  52932  20200303   70500       0.34.4               -1   
416  35191212587616712  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
316                -1           GALAXY     0.0904        CHH  ...  379.037092   
366                -1           GALAXY     0.0904        MJO  ...  379.037092   
416                -1           GALAXY     0.0904        AMA  ...  379.037092   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
316        0.0904         GALAXY              2.0       2  0.0         0.0904   
366        0.0904         GALAXY              2.0       2  0.0         0.0904   
416        0.0904            QSO              2.0       2  0.0         0.0904   

                                      all VI comments  N_VI  \
316  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   
366  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   
416  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   

                       merger comment  
316  Bad calibration. Secure emission  
366  Bad calibration. Secure emission  
416  Bad calibration. Secure emission  

[3 rows x 32 columns]

conflict ID =  43


In [109]:
#copy this text to a new cell to display the conflict
conflict_id=44
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
320  35191216513484015           GALAXY       0.29        CHH           1   
370  35191216513484015           GALAXY       0.29        MJO           1   
420  35191216513484015           GALAXY       0.29        AMA           3   

    VI_issue  VI_z VI_spectype  \
320      NaN   NaN         NaN   
370        R   NaN         NaN   
420        R  0.25         NaN   

                                            VI_comment  best redshift  \
320  no emission or absorption lines; bad continuum...           0.29   
370  bestfit seems not working for the continuum + ...           0.29   
420  one strong feature at 5860; could have possibl...           0.25   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z     dz  \
320        GALAXY          1.666667        2           0.29  0.032   
370        GALAXY          1.666667        2           0.29  0.032   
420        GALAXY          1.666667        2           0.29  0.032   

                                       all VI comments  N_VI merger comment  
320  no emission or absorption lines; bad continuum...     3           none  
370  no emission or absorption lines; bad continuum...     3           none  
420  no emission or absorption lines; bad continuum...     3           none

In [110]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.2030
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 1
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration. No Secure feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
320  35191216513484015  52932  20200303   70500       0.34.4               -1   
370  35191216513484015  52932  20200303   70500       0.34.4               -1   
420  35191216513484015  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
320                -1           GALAXY       0.29        CHH  ...  345.680393   
370                -1           GALAXY       0.29        MJO  ...  345.680393   
420                -1           GALAXY       0.29        AMA  ...  345.680393   

    best redshift  best spectype vi_combined_flag vi_diff     dz  \
320          0.29         GALAXY         1.666667       2  0.032   
370          0.29         GALAXY         1.666667       2  0.032   
420          0.25         GALAXY         1.666667       2  0.032   

     vi_combined_z                                    all VI comments  N_VI  \
320           0.29  no emission or absorption lines; bad continuum...     3   
370           0.29  no emission or absorption lines; bad continuum...     3   
420           0.29  no emission or absorption lines; bad continuum...     3   

                         merger comment  
320  Bad calibration. No Secure feature  
370  Bad calibration. No Secure feature  
420  Bad calibration. No Secure feature  

[3 rows x 32 columns]

conflict ID =  44


In [111]:
#copy this text to a new cell to display the conflict
conflict_id=45
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
322  35191216513485304           GALAXY     0.2991        CHH           1   
372  35191216513485304           GALAXY     0.2991        MJO           3   
422  35191216513485304           GALAXY     0.2991        AMA           3   

    VI_issue    VI_z VI_spectype  \
322      NaN     NaN         NaN   
372      NaN  0.1983         NaN   
422        R  0.3499         NaN   

                                            VI_comment  best redshift  \
322  no emission or absorption lines; bad continuum...         0.2991   
372                    (H&K +) G + MgI + D + Ha (+SII)         0.1983   
422                        possible incorrect redshift         0.3499   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
322        GALAXY          2.333333        2         0.2991  0.126513   
372        GALAXY          2.333333        2         0.2991  0.126513   
422        GALAXY          2.333333        2         0.2991  0.126513   

                                       all VI comments  N_VI merger comment  
322  no emission or absorption lines; bad continuum...     3           none  
372  no emission or absorption lines; bad continuum...     3           none  
422  no emission or absorption lines; bad continuum...     3           none

In [112]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.1983
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration.  Secure absorption feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
322  35191216513485304  52932  20200303   70500       0.34.4               -1   
372  35191216513485304  52932  20200303   70500       0.34.4               -1   
422  35191216513485304  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
322                -1           GALAXY     0.2991        CHH  ...  203.287277   
372                -1           GALAXY     0.2991        MJO  ...  203.287277   
422                -1           GALAXY     0.2991        AMA  ...  203.287277   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
322        0.1983         GALAXY         2.333333       2  0.126513   
372        0.1983         GALAXY         2.333333       2  0.126513   
422        0.1983         GALAXY         2.333333       2  0.126513   

     vi_combined_z                                    all VI comments  N_VI  \
322         0.2991  no emission or absorption lines; bad continuum...     3   
372         0.2991  no emission or absorption lines; bad continuum...     3   
422         0.2991  no emission or absorption lines; bad continuum...     3   

                                  merger comment  
322  Bad calibration.  Secure absorption feature  
372  Bad calibration.  Secure absorption feature  
422  Bad calibration.  Secure absorption feature  

[3 rows x 32 columns]

conflict ID =  45


In [113]:
#copy this text to a new cell to display the conflict
conflict_id=46
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
324  35191220401604151           GALAXY     1.0478        CHH           2   
374  35191220401604151           GALAXY     1.0478        MJO           4   
424  35191220401604151           GALAXY     1.0478        AMA           3   

    VI_issue    VI_z VI_spectype                            VI_comment  \
324      NaN     NaN         NaN  one emission line; bad continuum fit   
374        R  0.1628         NaN          H&K + G + MgI + D + Ha + SII   
424      NaN     NaN         NaN                                    --   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
324         1.0478        GALAXY               3.0        2         1.0478   
374         0.1628        GALAXY               3.0        2         1.0478   
424         1.0478        GALAXY               3.0        2         1.0478   

           dz                                    all VI comments  N_VI  \
324  0.761094  one emission line; bad continuum fit|H&K + G +...     3   
374  0.761094  one emission line; bad continuum fit|H&K + G +...     3   
424  0.761094  one emission line; bad continuum fit|H&K + G +...     3   

    merger comment  
324           none  
374           none  
424           none

In [114]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.1628
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration.  Secure emission feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
324  35191220401604151  52932  20200303   70500       0.34.4               -1   
374  35191220401604151  52932  20200303   70500       0.34.4               -1   
424  35191220401604151  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
324                -1           GALAXY     1.0478        CHH  ...  217.326645   
374                -1           GALAXY     1.0478        MJO  ...  217.326645   
424                -1           GALAXY     1.0478        AMA  ...  217.326645   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
324        0.1628         GALAXY              3.0       2  0.761094   
374        0.1628         GALAXY              3.0       2  0.761094   
424        0.1628         GALAXY              3.0       2  0.761094   

     vi_combined_z                                    all VI comments  N_VI  \
324         1.0478  one emission line; bad continuum fit|H&K + G +...     3   
374         1.0478  one emission line; bad continuum fit|H&K + G +...     3   
424         1.0478  one emission line; bad continuum fit|H&K + G +...     3   

                                merger comment  
324  Bad calibration.  Secure emission feature  
374  Bad calibration.  Secure emission feature  
424  Bad calibration.  Secure emission feature  

[3 rows x 32 columns]

conflict ID =  46


In [115]:
#copy this text to a new cell to display the conflict
conflict_id=47
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
325  35191220401605015           GALAXY     0.5069        CHH           1   
375  35191220401605015           GALAXY     0.5069        MJO           4   
425  35191220401605015           GALAXY     0.5069        AMA           3   

    VI_issue    VI_z VI_spectype    VI_comment  best redshift best spectype  \
325        C     NaN         NaN            --         0.5069        GALAXY   
375        R  0.1496         NaN  G + Ha + SII         0.1496        GALAXY   
425      NaN     NaN         NaN            --         0.5069        GALAXY   

     vi_combined_flag  vi_diff  vi_combined_z        dz     all VI comments  \
325          2.666667        3         0.5069  0.310804  --|G + Ha + SII|--   
375          2.666667        3         0.5069  0.310804  --|G + Ha + SII|--   
425          2.666667        3         0.5069  0.310804  --|G + Ha + SII|--   

     N_VI merger comment  
325     3           none  
375     3           none  
425     3           none

In [116]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.1496
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration.  Secure emission feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
325  35191220401605015  52932  20200303   70500       0.34.4               -1   
375  35191220401605015  52932  20200303   70500       0.34.4               -1   
425  35191220401605015  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
325                -1           GALAXY     0.5069        CHH  ...  17.758251   
375                -1           GALAXY     0.5069        MJO  ...  17.758251   
425                -1           GALAXY     0.5069        AMA  ...  17.758251   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
325        0.1496         GALAXY         2.666667       3  0.310804   
375        0.1496         GALAXY         2.666667       3  0.310804   
425        0.1496         GALAXY         2.666667       3  0.310804   

     vi_combined_z     all VI comments  N_VI  \
325         0.5069  --|G + Ha + SII|--     3   
375         0.5069  --|G + Ha + SII|--     3   
425         0.5069  --|G + Ha + SII|--     3   

                                merger comment  
325  Bad calibration.  Secure emission feature  
375  Bad calibration.  Secure emission feature  
425  Bad calibration.  Secure emission feature  

[3 rows x 32 columns]

conflict ID =  47


In [117]:
len(unique_targets)

55

In [118]:
#copy this text to a new cell to display the conflict
conflict_id=48
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
327  35191220401605130           GALAXY     0.2083        CHH           3   
377  35191220401605130           GALAXY     0.2083        MJO           4   
427  35191220401605130           GALAXY     0.2083        AMA           2   

    VI_issue  VI_z VI_spectype  \
327      NaN   NaN         NaN   
377      NaN   NaN         NaN   
427      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
327  possible Halpha; NII; possible H; K; Mg; D abs...         0.2083   
377                                  H&K Hd G MgI D Ha         0.2083   
427                                 no strong features         0.2083   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
327        GALAXY               3.0        2         0.2083  0.0   
377        GALAXY               3.0        2         0.2083  0.0   
427        GALAXY               3.0        2         0.2083  0.0   

                                       all VI comments  N_VI merger comment  
327  possible Halpha; NII; possible H; K; Mg; D abs...     3           none  
377  possible Halpha; NII; possible H; K; Mg; D abs...     3           none  
427  possible Halpha; NII; possible H; K; Mg; D abs...     3           none

In [119]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.1496
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration.  Secure  feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
327  35191220401605130  52932  20200303   70500       0.34.4               -1   
377  35191220401605130  52932  20200303   70500       0.34.4               -1   
427  35191220401605130  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
327                -1           GALAXY     0.2083        CHH  ...  40.067838   
377                -1           GALAXY     0.2083        MJO  ...  40.067838   
427                -1           GALAXY     0.2083        AMA  ...  40.067838   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
327        0.2083         GALAXY              3.0       2  0.0         0.2083   
377        0.2083         GALAXY              3.0       2  0.0         0.2083   
427        0.2083         GALAXY              3.0       2  0.0         0.2083   

                                       all VI comments  N_VI  \
327  possible Halpha; NII; possible H; K; Mg; D abs...     3   
377  possible Halpha; NII; possible H; K; Mg; D abs...     3   
427  possible Halpha; NII; possible H; K; Mg; D abs...     3   

                        merger comment  
327  Bad calibration.  Secure  feature  
377  Bad calibration.  Secure  feature  
427  Bad calibration.  Secure  feature  

[3 rows x 32 columns]

conflict ID =  48


In [120]:
#copy this text to a new cell to display the conflict
conflict_id=49
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
330  35191220409992975              QSO     1.6369        CHH           1   
380  35191220409992975              QSO     1.6369        MJO           4   
430  35191220409992975              QSO     1.6369        AMA           3   

    VI_issue    VI_z VI_spectype   VI_comment  best redshift best spectype  \
330        C     NaN         NaN           --         1.6369           QSO   
380       RC  0.2398      GALAXY  OII  Ha SII         0.2398        GALAXY   
430      NaN     NaN         NaN           --         1.6369           QSO   

     vi_combined_flag  vi_diff  vi_combined_z        dz    all VI comments  \
330          2.666667        3         1.6369  1.126875  --|OII  Ha SII|--   
380          2.666667        3         1.6369  1.126875  --|OII  Ha SII|--   
430          2.666667        3         1.6369  1.126875  --|OII  Ha SII|--   

     N_VI merger comment  
330     3           none  
380     3           none  
430     3           none

In [121]:
#copy this text to a new cell to resolve the conflict
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.2398
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Bad calibration.  Secure emission feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
330  35191220409992975  52932  20200303   70500       0.34.4               -1   
380  35191220409992975  52932  20200303   70500       0.34.4               -1   
430  35191220409992975  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
330                -1              QSO     1.6369        CHH  ...  10.986743   
380                -1              QSO     1.6369        MJO  ...  10.986743   
430                -1              QSO     1.6369        AMA  ...  10.986743   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
330        0.2398            QSO         2.666667       3  1.126875   
380        0.2398         GALAXY         2.666667       3  1.126875   
430        0.2398            QSO         2.666667       3  1.126875   

     vi_combined_z    all VI comments  N_VI  \
330         1.6369  --|OII  Ha SII|--     3   
380         1.6369  --|OII  Ha SII|--     3   
430         1.6369  --|OII  Ha SII|--     3   

                                merger comment  
330  Bad calibration.  Secure emission feature  
380  Bad calibration.  Secure emission feature  
430  Bad calibration.  Secure emission feature  

[3 rows x 32 columns]

conflict ID =  49


In [122]:
#copy this text to a new cell to display the conflict
conflict_id=50
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
331  35191220409993084           GALAXY     0.2603        CHH           4   
381  35191220409993084           GALAXY     0.2603        MJO           4   
431  35191220409993084           GALAXY     0.2603        AMA           2   

    VI_issue  VI_z VI_spectype                                  VI_comment  \
331      NaN   NaN         NaN  H; K; Mg; D absorption; good continuum fit   
381      NaN   NaN         NaN                                 H&K G MgI D   
431      NaN   NaN         NaN                          no strong features   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
331         0.2603        GALAXY          3.333333        2         0.2603   
381         0.2603        GALAXY          3.333333        2         0.2603   
431         0.2603        GALAXY          3.333333        2         0.2603   

      dz                                    all VI comments  N_VI  \
331  0.0  H; K; Mg; D absorption; good continuum fit|H&K...     3   
381  0.0  H; K; Mg; D absorption; good continuum fit|H&K...     3   
431  0.0  H; K; Mg; D absorption; good continuum fit|H&K...     3   

    merger comment  
331           none  
381           none  
431           none

In [123]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.2398
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] ='Secure absorption feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
331  35191220409993084  52932  20200303   70500       0.34.4               -1   
381  35191220409993084  52932  20200303   70500       0.34.4               -1   
431  35191220409993084  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
331                -1           GALAXY     0.2603        CHH  ...  897.324485   
381                -1           GALAXY     0.2603        MJO  ...  897.324485   
431                -1           GALAXY     0.2603        AMA  ...  897.324485   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
331        0.2603         GALAXY         3.333333       2  0.0         0.2603   
381        0.2603         GALAXY         3.333333       2  0.0         0.2603   
431        0.2603         GALAXY         3.333333       2  0.0         0.2603   

                                       all VI comments  N_VI  \
331  H; K; Mg; D absorption; good continuum fit|H&K...     3   
381  H; K; Mg; D absorption; good continuum fit|H&K...     3   
431  H; K; Mg; D absorption; good continuum fit|H&K...     3   

                merger comment  
331  Secure absorption feature  
381  Secure absorption feature  
431  Secure absorption feature  

[3 rows x 32 columns]

conflict ID =  50


In [124]:
#copy this text to a new cell to display the conflict
conflict_id=51
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
339  35191220414188015           GALAXY     0.6444        CHH           3   
389  35191220414188015           GALAXY     0.6444        MJO           4   
439  35191220414188015           GALAXY     0.6444        AMA           2   

    VI_issue  VI_z VI_spectype  \
339      NaN   NaN         NaN   
389      NaN   NaN         NaN   
439      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
339  OII; possible OIII emission lines; H; K absorp...         0.6444   
389                                       OII + H&K Hb         0.6444   
439                  no strong features; possible O ||         0.6444   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
339        GALAXY               3.0        2         0.6444  0.0   
389        GALAXY               3.0        2         0.6444  0.0   
439        GALAXY               3.0        2         0.6444  0.0   

                                       all VI comments  N_VI merger comment  
339  OII; possible OIII emission lines; H; K absorp...     3           none  
389  OII; possible OIII emission lines; H; K absorp...     3           none  
439  OII; possible OIII emission lines; H; K absorp...     3           none

In [125]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.2398
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] ='Secure  feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
339  35191220414188015  52932  20200303   70500       0.34.4               -1   
389  35191220414188015  52932  20200303   70500       0.34.4               -1   
439  35191220414188015  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
339                -1           GALAXY     0.6444        CHH  ...  445.812211   
389                -1           GALAXY     0.6444        MJO  ...  445.812211   
439                -1           GALAXY     0.6444        AMA  ...  445.812211   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
339        0.6444         GALAXY              3.0       2  0.0         0.6444   
389        0.6444         GALAXY              3.0       2  0.0         0.6444   
439        0.6444         GALAXY              3.0       2  0.0         0.6444   

                                       all VI comments  N_VI   merger comment  
339  OII; possible OIII emission lines; H; K absorp...     3  Secure  feature  
389  OII; possible OIII emission lines; H; K absorp...     3  Secure  feature  
439  OII; possible OIII emission lines; H; K absorp...     3  Secure  feature  

[3 rows x 32 columns]

conflict ID =  51


In [126]:
#copy this text to a new cell to display the conflict
conflict_id=52
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
342  35191220414188963           GALAXY     0.4126        CHH           2   
392  35191220414188963           GALAXY     0.4126        MJO           4   
442  35191220414188963           GALAXY     0.4126        AMA           2   

    VI_issue  VI_z VI_spectype  \
342      NaN   NaN         NaN   
392      NaN   NaN         NaN   
442      NaN   NaN         NaN   

                                            VI_comment  best redshift  \
342  no clear emission or absorption lines; good co...         0.4126   
392                               OII + H&K + MgI + Ha         0.4126   
442                                 no strong features         0.4126   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
342        GALAXY          2.666667        2         0.4126  0.0   
392        GALAXY          2.666667        2         0.4126  0.0   
442        GALAXY          2.666667        2         0.4126  0.0   

                                       all VI comments  N_VI merger comment  
342  no clear emission or absorption lines; good co...     3           none  
392  no clear emission or absorption lines; good co...     3           none  
442  no clear emission or absorption lines; good co...     3           none

In [127]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.2398
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 3
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] ='Secure  feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
342  35191220414188963  52932  20200303   70500       0.34.4               -1   
392  35191220414188963  52932  20200303   70500       0.34.4               -1   
442  35191220414188963  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
342                -1           GALAXY     0.4126        CHH  ...  1454.96858   
392                -1           GALAXY     0.4126        MJO  ...  1454.96858   
442                -1           GALAXY     0.4126        AMA  ...  1454.96858   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
342        0.4126         GALAXY         2.666667       2  0.0         0.4126   
392        0.4126         GALAXY         2.666667       2  0.0         0.4126   
442        0.4126         GALAXY         2.666667       2  0.0         0.4126   

                                       all VI comments  N_VI   merger comment  
342  no clear emission or absorption lines; good co...     3  Secure  feature  
392  no clear emission or absorption lines; good co...     3  Secure  feature  
442  no clear emission or absorption lines; good co...     3  Secure  feature  

[3 rows x 32 columns]

conflict ID =  52


In [128]:
#copy this text to a new cell to display the conflict
conflict_id=53
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
343  35191220414189411           GALAXY     0.7573        CHH           4   
393  35191220414189411           GALAXY     0.7573        MJO           4   
443  35191220414189411           GALAXY     0.7573        AMA           2   

    VI_issue  VI_z VI_spectype                               VI_comment  \
343      NaN   NaN         NaN                   H; K; Hbeta absorption   
393      NaN   NaN         NaN                            H&K + Hd + Hb   
443      NaN   NaN         NaN  possible absorption lines but very weak   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
343         0.7573        GALAXY          3.333333        2         0.7573   
393         0.7573        GALAXY          3.333333        2         0.7573   
443         0.7573        GALAXY          3.333333        2         0.7573   

      dz                                    all VI comments  N_VI  \
343  0.0  H; K; Hbeta absorption|H&K + Hd + Hb|possible ...     3   
393  0.0  H; K; Hbeta absorption|H&K + Hd + Hb|possible ...     3   
443  0.0  H; K; Hbeta absorption|H&K + Hd + Hb|possible ...     3   

    merger comment  
343           none  
393           none  
443           none

In [129]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.2398
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] ='Secure feature'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
343  35191220414189411  52932  20200303   70500       0.34.4               -1   
393  35191220414189411  52932  20200303   70500       0.34.4               -1   
443  35191220414189411  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
343                -1           GALAXY     0.7573        CHH  ...  444.642146   
393                -1           GALAXY     0.7573        MJO  ...  444.642146   
443                -1           GALAXY     0.7573        AMA  ...  444.642146   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
343        0.7573         GALAXY         3.333333       2  0.0         0.7573   
393        0.7573         GALAXY         3.333333       2  0.0         0.7573   
443        0.7573         GALAXY         3.333333       2  0.0         0.7573   

                                       all VI comments  N_VI  merger comment  
343  H; K; Hbeta absorption|H&K + Hd + Hb|possible ...     3  Secure feature  
393  H; K; Hbeta absorption|H&K + Hd + Hb|possible ...     3  Secure feature  
443  H; K; Hbeta absorption|H&K + Hd + Hb|possible ...     3  Secure feature  

[3 rows x 32 columns]

conflict ID =  53


In [130]:
conflict_id=54
show_spectra = True
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
347  35191220422576742           GALAXY     0.1983        CHH           2   
397  35191220422576742           GALAXY     0.1983        MJO           4   
447  35191220422576742           GALAXY     0.1983        AMA           3   

    VI_issue  VI_z VI_spectype                       VI_comment  \
347      NaN   NaN         NaN  no emission or absorption lines   
397      NaN   NaN         NaN                               --   
447      NaN   NaN         NaN                               --   

     best redshift best spectype  vi_combined_flag  vi_diff  vi_combined_z  \
347         0.1983        GALAXY               3.0        2         0.1983   
397         0.1983        GALAXY               3.0        2         0.1983   
447         0.1983        GALAXY               3.0        2         0.1983   

      dz                        all VI comments  N_VI merger comment  
347  0.0  no emission or absorption lines|--|--     3           none  
397  0.0  no emission or absorption lines|--|--     3           none  
447  0.0  no emission or absorption lines|--|--     3           none

Loading BokehJS ...

In [131]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift']= 0.2398
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 2
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best spectype'] = 

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] ='Bad calibration prevents confirmation of secure features. Be conservative'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
347  35191220422576742  52932  20200303   70500       0.34.4               -1   
397  35191220422576742  52932  20200303   70500       0.34.4               -1   
447  35191220422576742  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
347                -1           GALAXY     0.1983        CHH  ...  344.319406   
397                -1           GALAXY     0.1983        MJO  ...  344.319406   
447                -1           GALAXY     0.1983        AMA  ...  344.319406   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
347        0.1983         GALAXY              3.0       2  0.0         0.1983   
397        0.1983         GALAXY              3.0       2  0.0         0.1983   
447        0.1983         GALAXY              3.0       2  0.0         0.1983   

                           all VI comments  N_VI  \
347  no emission or absorption lines|--|--     3   
397  no emission or absorption lines|--|--     3   
447  no emission or absorption lines|--|--     3   

                                        merger comment  
347  Bad calibration prevents confirmation of secur...  
397  Bad calibration prevents confirmation of secur...  
447  Bad calibration prevents confirmation of secur...  

[3 rows x 32 columns]

conflict ID =  54


### and so on...

We should now recompute the conflicts, and not find any.

In [132]:
vi_conflict = VI.find_conflicts(vi_gp)

In [133]:
unique_targets = np.unique(vi_conflict['TARGETID'].tolist())
print('Targets with problematic VI: ', unique_targets)
print('Total number of conflicts to resolve: ', len(unique_targets))

Targets with problematic VI:  [35191200679988159 35191212587616712 35191220409992975]
Total number of conflicts to resolve:  3


Display anything that was missed (if "Total number of conflicts" isn't zero) and resolve!

In [134]:
#copy this text to a new cell to display the conflict
conflict_id=0
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
163  35191200679988159              QSO     1.1499        AMA           4   
213  35191200679988159              QSO     1.1499        MJO           4   
263  35191200679988159              QSO     1.1499        CHH           4   

    VI_issue    VI_z VI_spectype  \
163      NaN  1.0899         NaN   
213       RC  0.2699      GALAXY   
263        S     NaN         NaN   

                                            VI_comment  best redshift  \
163                                                 --         0.2699   
213  H&K + G + Hb + MgI + D + pipeline fit doesn't ...         0.2699   
263     no emission or absorption lines; bad continuum         0.2699   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z        dz  \
163           QSO          2.333333        3         1.1499  0.692968   
213        GALAXY          2.333333        3         1.1499  0.692968   
263           QSO          2.333333        3         1.1499  0.692968   

                                       all VI comments  N_VI  \
163  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   
213  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   
263  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   

                                       merger comment  
163  Bad calibration. absorption  features are secure  
213  Bad calibration. absorption  features are secure  
263  Bad calibration. absorption  features are secure

Loading BokehJS ...

In [136]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'best redshift'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'VI_quality'] = 4
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = 'Secure features. Bad calibration. Galaxy'

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)

TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
163  35191200679988159  52932  20200303   70500       0.34.4               -1   
213  35191200679988159  52932  20200303   70500       0.34.4               -1   
263  35191200679988159  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
163                -1              QSO     1.1499        AMA  ...  44.535669   
213                -1              QSO     1.1499        MJO  ...  44.535669   
263                -1              QSO     1.1499        CHH  ...  44.535669   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
163        0.2699         GALAXY         2.333333       3  0.692968   
213        0.2699         GALAXY         2.333333       3  0.692968   
263        0.2699         GALAXY         2.333333       3  0.692968   

     vi_combined_z                                    all VI comments  N_VI  \
163         1.1499  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   
213         1.1499  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   
263         1.1499  --|H&K + G + Hb + MgI + D + pipeline fit doesn...     3   

                               merger comment  
163  Secure features. Bad calibration. Galaxy  
213  Secure features. Bad calibration. Galaxy  
263  Secure features. Bad calibration. Galaxy  

[3 rows x 32 columns]

conflict ID =  0


In [137]:
#copy this text to a new cell to display the conflict
conflict_id=1
display_conflict(conflict_id, show_spectra=show_spectra)



TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
316  35191212587616712           GALAXY     0.0904        CHH           3   
366  35191212587616712           GALAXY     0.0904        MJO           3   
416  35191212587616712           GALAXY     0.0904        AMA           3   

    VI_issue  VI_z VI_spectype          VI_comment  best redshift  \
316      NaN   NaN         NaN    On emission line         0.0904   
366      NaN   NaN         NaN  Ha (+ SII) + Ca II         0.0904   
416        C   NaN         QSO        Possible QSO         0.0904   

    best spectype  vi_combined_flag  vi_diff  vi_combined_z   dz  \
316        GALAXY               2.0        2         0.0904  0.0   
366        GALAXY               2.0        2         0.0904  0.0   
416           QSO               2.0        2         0.0904  0.0   

                                      all VI comments  N_VI  \
316  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   
366  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   
416  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   

                       merger comment  
316  Bad calibration. Secure emission  
366  Bad calibration. Secure emission  
416  Bad calibration. Secure emission

Loading BokehJS ...

In [138]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.512
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'VI class'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = '4000 break '

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
316  35191212587616712  52932  20200303   70500       0.34.4               -1   
366  35191212587616712  52932  20200303   70500       0.34.4               -1   
416  35191212587616712  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...   DELTACHI2  \
316                -1           GALAXY     0.0904        CHH  ...  379.037092   
366                -1           GALAXY     0.0904        MJO  ...  379.037092   
416                -1           GALAXY     0.0904        AMA  ...  379.037092   

    best redshift  best spectype vi_combined_flag vi_diff   dz  vi_combined_z  \
316        0.0904         GALAXY              2.0       2  0.0         0.0904   
366        0.0904         GALAXY              2.0       2  0.0         0.0904   
416        0.0904         GALAXY              2.0       2  0.0         0.0904   

                                      all VI comments  N_VI  \
316  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   
366  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   
416  On emission line|Ha (+ SII) + Ca II|Possible QSO     3   

                       merger comment  
316  Bad calibration. Secure emission  
366  Bad calibration. Secure emission  
416  Bad calibration. Secure emission  

[3 rows x 32 columns]

conflict ID =  1


In [139]:
#copy this text to a new cell to display the conflict
conflict_id=2
display_conflict(conflict_id, show_spectra=show_spectra)


TARGETID Redrock_spectype  Redrock_z VI_scanner  VI_quality  \
330  35191220409992975              QSO     1.6369        CHH           4   
380  35191220409992975              QSO     1.6369        MJO           4   
430  35191220409992975              QSO     1.6369        AMA           4   

    VI_issue    VI_z VI_spectype   VI_comment  best redshift best spectype  \
330        C     NaN         NaN           --         0.2398           QSO   
380       RC  0.2398      GALAXY  OII  Ha SII         0.2398        GALAXY   
430      NaN     NaN         NaN           --         0.2398           QSO   

     vi_combined_flag  vi_diff  vi_combined_z        dz    all VI comments  \
330          2.666667        3         1.6369  1.126875  --|OII  Ha SII|--   
380          2.666667        3         1.6369  1.126875  --|OII  Ha SII|--   
430          2.666667        3         1.6369  1.126875  --|OII  Ha SII|--   

     N_VI                             merger comment  
330     3  Bad calibration.  Secure emission feature  
380     3  Bad calibration.  Secure emission feature  
430     3  Bad calibration.  Secure emission feature

Loading BokehJS ...

In [140]:
#copy this text to a new cell to resolve the conflict
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best redshift'] = 0.512
#vi.loc[vi.TargetID==unique_targets[conflict_id], 'VI class'] = 
vi.loc[vi.TARGETID==unique_targets[conflict_id], 'best spectype'] = 'GALAXY'

#add a comment
#vi.loc[vi.TARGETID==unique_targets[conflict_id], 'merger comment'] = '4000 break '

#look at the values again to make sure all is well
display(vi[vi.TARGETID==unique_targets[conflict_id]])
print('conflict ID = ', conflict_id)


TARGETID  EXPID     NIGHT  TILEID Spec_version  Redrock_version  \
330  35191220409992975  52932  20200303   70500       0.34.4               -1   
380  35191220409992975  52932  20200303   70500       0.34.4               -1   
430  35191220409992975  52932  20200303   70500       0.34.4               -1   

     Template_version Redrock_spectype  Redrock_z VI_scanner  ...  DELTACHI2  \
330                -1              QSO     1.6369        CHH  ...  10.986743   
380                -1              QSO     1.6369        MJO  ...  10.986743   
430                -1              QSO     1.6369        AMA  ...  10.986743   

    best redshift  best spectype vi_combined_flag vi_diff        dz  \
330        0.2398         GALAXY         2.666667       3  1.126875   
380        0.2398         GALAXY         2.666667       3  1.126875   
430        0.2398         GALAXY         2.666667       3  1.126875   

     vi_combined_z    all VI comments  N_VI  \
330         1.6369  --|OII  Ha SII|--     3   
380         1.6369  --|OII  Ha SII|--     3   
430         1.6369  --|OII  Ha SII|--     3   

                                merger comment  
330  Bad calibration.  Secure emission feature  
380  Bad calibration.  Secure emission feature  
430  Bad calibration.  Secure emission feature  

[3 rows x 32 columns]

conflict ID =  2


Let's check the number of conflicts again.

In [141]:
vi_conflict = VI.find_conflicts(vi_gp)

In [142]:
unique_targets = np.unique(vi_conflict['TARGETID'].tolist())
print('Targets with problematic VI: ', unique_targets)
print('Total number of conflicts to resolve: ', len(unique_targets))

Targets with problematic VI:  []
Total number of conflicts to resolve:  0


## Woohoo!

## Finally
we need to recompute vi_combined_flag and vi_combined_z, after everything is resolved.

In [143]:
vi['vi_combined_flag'] = vi.groupby('TARGETID')['VI_quality'].transform('mean')
vi['vi_combined_z'] = vi.groupby('TARGETID')['best redshift'].transform('mean')


## Now we prepare to write to file. 

### The important columns for the truth table construction are **vi_combined_flag** and **vi_combined_z** 

The truth table should **take the redhift value in vi_combined_z** for all objects with **vi_combined_flag >= 2.5** (for discussion, but this catches the cases where there is some disagreement on the 2/3 boundary).

After the merging process, those two columns will be the same for ALL of the members of each group by TargetID, so it doesn't matter which member we write to file. Taking the 1st one just makes this easy. 


In [144]:
vi.keys()

Index(['TARGETID', 'EXPID', 'NIGHT', 'TILEID', 'Spec_version',
       'Redrock_version', 'Template_version', 'Redrock_spectype', 'Redrock_z',
       'VI_scanner', 'VI_quality', 'VI_issue', 'VI_z', 'VI_spectype',
       'VI_comment', 'FIBER', 'FLUX_G', 'FLUX_R', 'FLUX_Z', 'FIBERFLUX_G',
       'FIBERFLUX_R', 'FIBERFLUX_Z', 'DELTACHI2', 'best redshift',
       'best spectype', 'vi_combined_flag', 'vi_diff', 'dz', 'vi_combined_z',
       'all VI comments', 'N_VI', 'merger comment'],
      dtype='object')

In [145]:
print(VI_dir+save_filename)

/global/homes/t/tlan/projects/VI_files/Andes_reinspection/BGS/truth_table_Andes_reinspection_BGS_70500_20200303_1


In [146]:
vi_gp['Redrock_z', 'Redrock_spectype', 'best redshift' , 'best spectype', 'vi_combined_flag',  
      'all VI comments', 'merger comment', 'N_VI', 'DELTACHI2','FIBER'].first().to_csv(VI_dir+save_filename)

<ipython-input-146-2063ed20beca>:1: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  vi_gp['Redrock_z', 'Redrock_spectype', 'best redshift' , 'best spectype', 'vi_combined_flag',


Check that merged file reads in OK - check comments

In [147]:
merged_file = pd.read_csv(VI_dir+save_filename)

In [148]:
merged_file.keys()

Index(['TARGETID', 'Redrock_z', 'Redrock_spectype', 'best redshift',
       'best spectype', 'vi_combined_flag', 'all VI comments',
       'merger comment', 'N_VI', 'DELTACHI2', 'FIBER'],
      dtype='object')

In [149]:
merged_file

TARGETID  Redrock_z Redrock_spectype  best redshift  \
0    35191196661843077     0.2732           GALAXY         0.2732   
1    35191196661843440     0.2080           GALAXY         0.2080   
2    35191196661844537     0.4338           GALAXY         0.4338   
3    35191196661845406     0.2381           GALAXY         0.2381   
4    35191196666036608     1.1471              QSO         1.1471   
..                 ...        ...              ...            ...   
145  35191220418382799     0.1521           GALAXY         0.1521   
146  35191220418383876     0.1148           GALAXY         0.1148   
147  35191220422576742     0.1983           GALAXY         0.1983   
148  35191220422577184     0.1340           GALAXY         0.1340   
149  35191220422577218     0.1876           GALAXY         0.1876   

    best spectype  vi_combined_flag  \
0          GALAXY          4.000000   
1          GALAXY          3.333333   
2          GALAXY          4.000000   
3          GALAXY          3.333333   
4             QSO          1.333333   
..            ...               ...   
145        GALAXY          3.666667   
146        GALAXY          3.666667   
147        GALAXY          2.000000   
148        GALAXY          4.000000   
149        GALAXY          3.666667   

                                       all VI comments  \
0    --|possible H alpha emission feature; no 4000 ...   
1    Dn4000 + Continuum|Many weak absorption featur...   
2    Halpha; SII; OII lines|--|H&K + Ha + SII (+ G ...   
3    H;K absorption + continuum|Strong continuum; w...   
4        strange spectra|No C ||| or Mg || features|--   
..                                                 ...   
145  OII; Halpha; SII emission lines|seems OII doub...   
146  OII; Halpha emission lines; possible H; K; D a...   
147              no emission or absorption lines|--|--   
148  OII; Halpha; SII emission lines|OII doublet re...   
149  Hbeta; OIII; Halpha; SII emission liens; H; K ...   

                                        merger comment  N_VI    DELTACHI2  \
0    disagreement in quality. redshift is secure. H...     3    66.652988   
1                                                 none     3   348.863147   
2                                                 none     3   673.106780   
3                                                 none     3  1130.680205   
4                                                 none     3   100.769188   
..                                                 ...   ...          ...   
145                                               none     3   837.397658   
146                                               none     3   957.042863   
147  Bad calibration prevents confirmation of secur...     3   344.319406   
148                                               none     3  1414.918964   
149                                               none     3   371.857344   

     FIBER  
0      356  
1      363  
2      362  
3      380  
4      485  
..     ...  
145   1706  
146   1740  
147   1515  
148   1543  
149   1508  

[150 rows x 11 columns]

In [ ]:
VI_dir